## cik==1422183 scratch work


In [72]:
import re
import pandas as pd
import numpy as np
import platform
from utils import arguements,init_logger,ROOT_PATH
from fuzzywuzzy import process

def get_standard_name(col, choices, score_cutoff=60):
    best_match, score = process.extractOne(col, choices)
    if score > score_cutoff:
        return best_match
    return col
            
def merge_duplicate_columns(
    df:pd.DataFrame,
)->pd.DataFrame:
    duplicate_cols = df.columns[df.columns.duplicated(keep=False)]
    for col_name in duplicate_cols.unique():
        duplicate_data = df.loc[:, df.columns == col_name]
        merged_data = duplicate_data.apply(lambda row: ' '.join(set(row.dropna().astype(str))), axis=1)
        df = df.loc[:, df.columns != col_name]
        df[col_name] = merged_data
    return df

def standard_field_names()->tuple:
    return (
        'portfolio',
        'footnotes',
        'industry',
        'rate',
        'floor',
        'maturity',
        'principal amount', # TODO change stand names for more dynamic fuzzywuzzy matching
        'cost',
        'value',
        'investment',
        'date',
        'subheaders',
        'number of shares'
    )

def common_subheaders()->tuple:
    return (
        'senior secured loans',
        'first lien',
        'second lien',
        'senior secured bonds',
        'subordinated debt',
        'equity/other',
        'collateralized securities',
        'preferred equity—',
        'control investments',
        'affiliated investments',
        'non-control/non-affilate investments'
    )
    
def strip_string(
    columns_names:list,
    standardize:bool=False
)->tuple:
    columns = tuple(map(lambda col:re.sub(r'[^a-z]', '', str(col).lower()),columns_names))
    if standardize:
        standard_fields = standard_field_names()
        return tuple(
            get_standard_name(col,standard_fields) for col in columns
        )
    return columns

def concat(*dfs)->list:
    final = []
    for df in dfs:
        final.extend(df.values.tolist())
    return final

def get_key_fields(
    df_cur:pd.DataFrame
)->tuple:
    important_fields = standard_field_names() + common_subheaders()
    for idx,row in enumerate(df_cur.iterrows()):
        found = any(any(
            key in str(field).lower() 
            for key in important_fields)
                    for field in row[-1].dropna().tolist()
            )
        if found and len(set(row[-1].dropna().tolist())) >= 5:
            fields = strip_string(row[-1].tolist(),standardize=found) ,idx
            return fields
    return strip_string(df_cur.iloc[0].tolist(),standardize=found),0



def extract_subheaders(
    df:pd.DataFrame,
)->pd.DataFrame:
    include = df.apply(
    lambda row: row.astype(str).str.contains('|'.join(common_subheaders()), case=False, na=False).any(),
        axis=1) # 
    
    exclude = ~df.apply(
        lambda row: row.astype(str).str.contains('total', case=False, na=False).any(),
        axis=1
    )
    
    idx = df[include & exclude].index.tolist()
    df['subheaders'] = 'no_subheader'
    
    if not idx:
        return df
    
    df.loc[idx[-1]:,'subheaders'] = df.iloc[idx[-1],1] if isinstance(df.iloc[idx[-1],0],float)  else df.iloc[idx[-1],0]
    for j,i in enumerate(idx[:-1]):
        subheader = df.iloc[i,1] if isinstance(df.iloc[i,0],float)  else df.iloc[i,0]
        df.loc[idx[j]:idx[j+1],'subheaders'] = subheader
    df.drop(idx,axis=0,inplace=True,errors='ignore') # drop subheader row
    return df

#TODO is number of shares = principal amount
def clean(
    file:str,
)->list:
    dirs = file.split('/') if platform.system() == "Linux" else file.split('\\')
    if  len(dirs) < 3 or '.csv' not in dirs[-1]:
        return
    df_cur = pd.read_csv(file,encoding='utf-8')
    df_cur = df_cur.T.drop_duplicates().T
    if df_cur.shape[1] < 4:
        return
    if df_cur.empty:
        return
    
    df_cur.reset_index(drop=True,inplace=True)
    
    important_fields,idx = get_key_fields(df_cur)
    if len(set(important_fields) - {''}) < 4:
        df_cur.replace('\u200b', np.nan, regex=True,inplace=True)
        df_cur.replace(r'\$|€|£',np.nan,regex=True,inplace=True)
        columns_to_drop = df_cur.notna().sum() == 1 #or df_cur.applymap(lambda x: ('$' == x)).any()
        return df_cur.iloc[:,1:].drop(columns=columns_to_drop[columns_to_drop].index)
    
    df_cur.columns = important_fields
    df_cur = merge_duplicate_columns(df_cur)
    cols_to_drop = [
        col for col in df_cur.columns.tolist() 
        if col == '' or col == 'nan'
    ] 

    df_cur.drop(columns=cols_to_drop, errors='ignore',inplace=True) # drop irrelevant columns
    return df_cur

## cik==1396440

In [74]:
import platform
from selenium import webdriver
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.common.by import By
from selenium.webdriver.support import expected_conditions as EC
# from selenium.webdriver.firefox.options import Options
from selenium.webdriver.chrome.options import Options

url = 'https://www.sec.gov/edgar/browse/?CIK=1396440'
options = Options()
options.binary_location = r'C:\Program Files\Google\Chrome\Application\chrome.exe'
driver = webdriver.Chrome(executable_path="chromedriver_win32/chromedriver.exe") \
    if platform.system() == "Linux" else webdriver.Chrome(options=options)
driver.get(url)
h5_tags = driver.find_elements(By.TAG_NAME,value='h5')

for h5_tag in h5_tags:
    if h5_tag.text == "[+] 10-K (annual reports) and 10-Q (quarterly reports)":
        # Click on the h5 tag.
        h5_tag.click()
        break
xpath = '//button[text()="View all 10-Ks and 10-Qs"]'
element = WebDriverWait(driver,3).until(EC.element_to_be_clickable((By.XPATH,xpath)))
driver.execute_script("arguments[0].click();", element)

conditions = '@data-original-title="Open document" and contains(@href, "Archive") and not(contains(@href, "index")) and not(contains(@href, "xml"))'
table = driver.find_elements(By.CSS_SELECTOR,value='div.dataTables_scroll')

_from = driver.find_elements(By.ID,value='filingDateFrom')
_to = driver.find_elements(By.ID,value='filingDateTo')
_from[0].clear();_to[0].clear()


In [2]:
import os
import glob
import re
import warnings
import datetime
import pandas as pd 
import numpy as np

warnings.simplefilter(action='ignore', category=FutureWarning)

def date_exceptions()->tuple:
    return (
        datetime.datetime(2017, 3, 31),
        datetime.datetime(2017, 6, 30),
        datetime.datetime(2017, 9, 30),
        datetime.datetime(2017, 12, 31),
        datetime.datetime(2018, 3, 31),
        datetime.datetime(2018, 6, 30),
        datetime.datetime(2018, 9, 30),
        datetime.datetime(2018, 12, 31),
    )

# TODO fix stopping criteria
def stopping_criterion(
    qtr:str,
    date_format:str='%Y-%m-%d'
)->str:
    qtr = datetime.datetime.strptime(qtr, date_format)
    if qtr <= datetime.datetime(2010, 3, 31) or qtr >= datetime.datetime(2017,3, 31):
        return '{}|{}'.format(r'^(?!.*\bSubtotal\b)(?=.*\btotal investments\b).+$',r'(?<!\S)Total\s+Portfolio\s+Investments')
    return '{}|{}'.format(r'^(?!.*\bSubtotal\b)(?=.*\btotal investments\b).+$',r'^(?!.*\bSubtotal\b)(?=.*\bTotal Idle Fund Investments).+$')


def common_subheaders()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        ('senior secured loans',
        'first lien',
        'second lien',
        'senior secured bonds',
        'subordinated debt',
        'equity/other',
        'collateralized securities',
        'preferred equity—',
        'Equity/Warrants',
        'unsecured debt',
        'senior secured notes',
        'warrants',
        'total senior secured first lien term loans',
        'secured debt')
    ))

def company_control_headers()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        (
        'control investments',
        'affiliate investments',
        'non-control/non-affilate investments',
        'Non-Controlled/Non-Affiliated  Investments:',
        'Affiliated  Investments:',
        'Non-Controlled/Non-Affiliated  Investments  :',
        'Affiliated  Investments  :',
        'Non-controlled/Non-affiliated Investments',
        'Affiliated Investments',
        )
    ))

# Function to extract date and convert to datetime object
def extract_date(file_path):
    # Extract date from file path (assuming date is always in 'YYYY-MM-DD' format)
    date_str = re.search(r'\d{4}-\d{2}-\d{2}', file_path).group()
    return datetime.datetime.strptime(date_str, '%Y-%m-%d')

def extract_subheaders(
    df:pd.DataFrame,
    control:bool,
)->pd.DataFrame:
    col_name = 'company_control' if control else 'TypeofInvestment'
    if col_name in df.columns:
        return df
    include = df.apply(
        lambda row: re.search('|'.join(company_control_headers() if control else common_subheaders()), str(row[0]), re.IGNORECASE) is not None ,
        axis=1
    )  
    
    exclude = ~df.apply(
        lambda row: row.astype(str).str.contains('total', case=False, na=False).any(),
        axis=1
    )
    idx = df[include & exclude].index.tolist()
    df[col_name] = None
    if not idx:
        return df

    prev_header = subheader = None
    df.loc[idx[-1]:,col_name] = df.iloc[idx[-1],1] if isinstance(df.iloc[idx[-1],0],float)  else df.iloc[idx[-1],0]
    for j,i in enumerate(idx[:-1]):
        prev_header = subheader
        subheader = df.iloc[i,1] if isinstance(df.iloc[i,0],float)  else df.iloc[i,0]
        df.loc[idx[j]:idx[j+1],col_name] = subheader if subheader != '' else prev_header
    # df.drop(idx,axis=0,inplace=True,errors='ignore') 
    return df


def merge_duplicate_columns(
    df:pd.DataFrame,
)->pd.DataFrame:
    duplicate_cols = df.columns[df.columns.duplicated(keep=False)]
    for col_name in duplicate_cols.unique():
        duplicate_data = df.loc[:, df.columns == col_name]
        merged_data = duplicate_data.apply(lambda row: ' '.join(set(row.dropna().astype(str))), axis=1)
        df = df.loc[:, df.columns != col_name]
        df[col_name] = merged_data
    return df

def remove_row_duplicates(row):
    seen = set()
    return pd.Series([x if x not in seen and not seen.add(x) else None for x in row])

def concat(*dfs)->list:
    final = []
    for df in dfs:
        final.extend(df.values.tolist())
    return final

def _clean_qtr(
    file_path:str
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0)
    df.replace(['\u200b','',')',':','$','%',0],np.nan,inplace=True) #':','$','%'
    df.dropna(axis=1,how='all',inplace=True)
    df.dropna(axis=0,how='all',inplace=True)
    
    cols = df.iloc[0].str.replace('[^a-zA-Z]', '', regex=True)
    if ((cols == '') + (cols == 'nan') + (cols == np.nan) + (cols == 'NaN')).sum() > 1:
        df = df.apply(remove_row_duplicates, axis=1)
    else:
        df.columns = cols
    df = merge_duplicate_columns(df.reset_index(drop=True))
    df.replace(['\u200b','',')',':','$','%',0],np.nan,inplace=True) #':','$','%'
    if ((cols == '') + (cols == 'nan') + (cols == np.nan) + (cols == 'NaN')).sum() > 1:
        df.dropna(axis=1,how='all',inplace=True)
        df.dropna(axis=0,how='all',inplace=True)
    df.drop(columns=df.columns[pd.isna(df.columns)].tolist() + [col for col in df.columns if col == ''],axis=1,inplace=True)
    return df


cik = 1396440
ROOT_PATH = r'C:\Users\pysol\Desktop\projects\sec_filings'

def main()->None:
    bdc = os.path.join(ROOT_PATH,str(cik))
    qtrs = os.listdir(bdc)
    for qtr in qtrs:
        if '.csv' in qtr or '.py' in qtr:
            continue
        # qtr = '2013-06-30'
        print(qtr)
        index_list_sum = 0
        i = 1
        df = _clean_qtr( os.path.join(bdc,qtr,f'Schedule_of_Investments_{i - 1}.csv'))
        col = df.columns.tolist()
        dfs = [df]
        while index_list_sum == 0:
            qtr_file = os.path.join(bdc,qtr,f'Schedule_of_Investments_{i}.csv')
            print(qtr_file)
            df = _clean_qtr(qtr_file)
            df.columns = col
            dfs.append(df)
            index_list = df.apply(
                lambda row:row.astype(str).str.contains(stopping_criterion(qtr), case=False, na=False).any(),
                axis=1
            )
            index_list_sum = index_list.sum()
            i += 1
        date_final = pd.concat(dfs,axis=0,ignore_index=True)#pd.DataFrame(concat(*dfs))   
        # Create a dictionary for renaming columns
        rename_dict = {col: 'portfoliocompany' for col in df.columns if 'portfolio' in col.lower()}
        
        date_final.rename(columns=rename_dict, inplace=True)
        date_final = date_final[['portfoliocompany']+[col for col in date_final.columns if col != 'portfoliocompany' ]]
        date_final = extract_subheaders(date_final,control=True)
        date_final = extract_subheaders(date_final,control=False)
        date_final['qtr'] = qtr.split('\\')[-1]
        for i in range(3):
            date_final[date_final.columns[i]].fillna(method='ffill',inplace=True)
        if not os.path.exists(os.path.join(bdc,qtr,'output')):
            os.makedirs(os.path.join(bdc,qtr,'output'))
        date_final.to_csv(os.path.join(bdc,qtr,'output',f'{qtr}.csv'),index=False)
        # break
    # Use glob to find files
    files = sorted(glob.glob(f'{cik}/*/output/*.csv'), key=extract_date)
    single_truth = pd.concat([
        pd.read_csv(df) for df in files
    ],axis=0,ignore_index=True)
    single_truth.to_csv(os.path.join(str(cik),f'{cik}_soi_table.csv'),index=False)


# from utils import init_logger
import warnings

# Suppress future warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.filterwarnings('ignore', category=pd.errors.SettingWithCopyWarning)    
main()

2007-09-30
C:\Users\pysol\Desktop\projects\sec_filings\1396440\2007-09-30\Schedule_of_Investments_1.csv
C:\Users\pysol\Desktop\projects\sec_filings\1396440\2007-09-30\Schedule_of_Investments_2.csv
2007-12-31
C:\Users\pysol\Desktop\projects\sec_filings\1396440\2007-12-31\Schedule_of_Investments_1.csv
C:\Users\pysol\Desktop\projects\sec_filings\1396440\2007-12-31\Schedule_of_Investments_2.csv
2008-03-31
C:\Users\pysol\Desktop\projects\sec_filings\1396440\2008-03-31\Schedule_of_Investments_1.csv
C:\Users\pysol\Desktop\projects\sec_filings\1396440\2008-03-31\Schedule_of_Investments_2.csv
2008-06-30
C:\Users\pysol\Desktop\projects\sec_filings\1396440\2008-06-30\Schedule_of_Investments_1.csv
C:\Users\pysol\Desktop\projects\sec_filings\1396440\2008-06-30\Schedule_of_Investments_2.csv
2008-09-30
C:\Users\pysol\Desktop\projects\sec_filings\1396440\2008-09-30\Schedule_of_Investments_1.csv
C:\Users\pysol\Desktop\projects\sec_filings\1396440\2008-09-30\Schedule_of_Investments_2.csv
C:\Users\pysol\

In [26]:
file_path = r'C:\Users\pysol\Desktop\projects\sec_filings\1396440\2018-09-30\Schedule_of_Investments_48.csv'

# TODO fix stopping criteria
def stopping_criterion(
    qtr:str,
    date_format:str='%Y-%m-%d'
)->str:
    qtr = datetime.datetime.strptime(qtr, date_format)
    if qtr <= datetime.datetime(2010, 3, 31) or qtr in date_exceptions():
        return '{}|{}'.format(r'^(?!.*\bSubtotal\b)(?=.*\btotal investments\b).+$',r'(?<!\S)Total\s+Portfolio\s+Investments')
    return '{}|{}'.format(r'^(?!.*\bSubtotal\b)(?=.*\btotal investments\b).+$',r'^(?!.*\bSubtotal\b)(?=.*\bTotal Idle Fund Investments).+$')

    
def _clean_qtr(
    file_path:str
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0)
    df.replace(['\u200b','',')',':','$','%',0],np.nan,inplace=True) #':','$','%'
    df.dropna(axis=1,how='all',inplace=True)
    df.dropna(axis=0,how='all',inplace=True)
    
    cols = df.iloc[0].str.replace('[^a-zA-Z]', '', regex=True)
    if ((cols == '') + (cols == 'nan') + (cols == np.nan) + (cols == 'NaN')).sum() > int(file_path.split('\\')[-3] == '1396440'):
        df = df.apply(remove_row_duplicates, axis=1)
    else:
        df.columns = cols
    df = merge_duplicate_columns(df.reset_index(drop=True))
    df.replace(['\u200b','',')',':','$','%',0],np.nan,inplace=True) #':','$','%'
    if ((cols == '') + (cols == 'nan') + (cols == np.nan) + (cols == 'NaN')).sum() > int(file_path.split('\\')[-3] == '1396440'):
        df.dropna(axis=1,how='all',inplace=True)
        df.dropna(axis=0,how='all',inplace=True)
    df.drop(columns=df.columns[pd.isna(df.columns)].tolist() + [col for col in df.columns if col == ''],axis=1,inplace=True)
    return df

df = _clean_qtr(file_path)
index_list = df.apply(
    lambda row:row.astype(str).str.contains(stopping_criterion('2010-03-31'), case=False, na=False).any(),
    axis=1
)
index_list_sum = index_list.sum()
index_list_sum

1

In [27]:
df

1                                    PortfolioCompany  \
0                            Portfolio Company(1)(20)   
1                       US Joiner Holding Company(11)   
2                                                 NaN   
3                       VIP Cinema Holdings, Inc.(11)   
4                                                 NaN   
5                              Vistar Media, Inc.(10)   
6                                                 NaN   
7                                                 NaN   
8                                                 NaN   
9                                   Wellnext, LLC(10)   
10                                                NaN   
11                  Wireless Vision Holdings, LLC(10)   
12                                                NaN   
13                                   Wirepath LLC(11)   
14                                                NaN   
15                              Zilliant Incorporated   
16                                                NaN   
17                                                NaN   
18                                                NaN   
19  Subtotal Non-Control/Non-Affiliate Investments...   
20     Total Portfolio Investments, December 31, 2017   

1                                      InvestmentDate  \
0                                 Investment Date(28)   
1                                      April 23, 2014   
2                                                 NaN   
3                                       March 9, 2017   
4                                                 NaN   
5                                   February 17, 2017   
6                                                 NaN   
7                                                 NaN   
8                                                 NaN   
9                                        May 23, 2016   
10                                                NaN   
11                                 September 29, 2017   
12                                                NaN   
13                                    August 16, 2017   
14                                                NaN   
15                                      June 15, 2012   
16                                                NaN   
17                                                NaN   
18                                                NaN   
19  Subtotal Non-Control/Non-Affiliate Investments...   
20     Total Portfolio Investments, December 31, 2017   

1                                 BusinessDescription  \
0                                Business Description   
1             Marine Interior Design and Installation   
2                                                 NaN   
3   Supplier of Luxury Seating to the Cinema Industry   
4                                                 NaN   
5   Operator of Digital Out-of-Home Advertising Pl...   
6                                                 NaN   
7                                                 NaN   
8                                                 NaN   
9            Manufacturer of Supplements and Vitamins   
10                                                NaN   
11  Provider of Wireless Telecommunications Carrie...   
12                                                NaN   
13     E-Commerce Provider into Connected Home Market   
14                                                NaN   
15  Price Optimization and Margin Management Solut...   
16                                                NaN   
17                                                NaN   
18                                                NaN   
19  Subtotal Non-Control/Non-Affiliate Investments...   
20     Total Portfolio Investments, December 31, 2017   

1                                    TypeofInvestment  \
0                        Type of Investment(2)(3)(27)   
1                                                 NaN   
2   LIBOR Plus 6.00% (Floor 1.00%), Current Coupon...   
3      

## cik==1490349

In [79]:

import os
import glob
import warnings
import re
import datetime
import pandas as pd 
import numpy as np

def stopping_criterion(
    search_string:str='total investments'
)->str:
    # Regular expression to ignore whitespace and case
    regex_pattern = search_string.replace(' ', r'\s*')
    return '{}|{}'.format(regex_pattern,'Invesmtents')

def concat(*dfs)->list:
    final = []
    for df in dfs:
        final.extend(df.values.tolist())
    return final

def common_subheaders()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        ('senior secured loans',
        'first lien',
        'second lien',
        'senior secured bonds',
        'subordinated debt',
        'equity/other',
        'collateralized securities',
        'preferred equity—',
        'Equity/Warrants',
        'unsecured debt',
        'senior secured notes',
        'warrants',
        'total senior secured first lien term loans')
    ))

def company_control_headers()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        (
        'control investments',
        'affiliate investments',
        'non-control/non-affilate investments',
        'Non-Controlled/Non-Affiliated  Investments:',
        'Affiliated  Investments:',
        'Non-Controlled/Non-Affiliated  Investments  :',
        'Affiliated  Investments  :',
        'Non-controlled/Non-affiliated Investments',
        'Affiliated Investments',
        )
    ))

# Function to extract date and convert to datetime object
def extract_date(file_path):
    # Extract date from file path (assuming date is always in 'YYYY-MM-DD' format)
    date_str = re.search(r'\d{4}-\d{2}-\d{2}', file_path).group()
    return datetime.datetime.strptime(date_str, '%Y-%m-%d')

def remove_row_duplicates(row):
    seen = set()
    return pd.Series([x if x not in seen and not seen.add(x) else None for x in row])

def merge_duplicate_columns(
    df:pd.DataFrame,
)->pd.DataFrame:
    duplicate_cols = df.columns[df.columns.duplicated(keep=False)]
    for col_name in duplicate_cols.unique():
        duplicate_data = df.loc[:, df.columns == col_name]
        merged_data = duplicate_data.apply(lambda row: ' '.join(set(row.dropna().astype(str))), axis=1)
        df = df.loc[:, df.columns != col_name]
        df[col_name] = merged_data
    return df

def extract_subheaders(
    df:pd.DataFrame,
    control:bool,
)->pd.DataFrame:
    col_name = 'company_control' if control else 'TypeofInvestment'
    if col_name in df.columns:
        return df
    include = df.apply(
        lambda row: re.search('|'.join(company_control_headers() if control else common_subheaders()), str(row[0]), re.IGNORECASE) is not None,
        axis=1
    )  
    
    exclude = ~df.apply(
        lambda row: row.astype(str).str.contains('total', case=False, na=False).any(),
        axis=1
    )
    idx = df[include & exclude].index.tolist()
    df[col_name] = None
    if not idx:
        return df

    prev_header = subheader = None
    df.loc[idx[-1]:,col_name] = df.iloc[idx[-1],1] if isinstance(df.iloc[idx[-1],0],float)  else df.iloc[idx[-1],0]
    for j,i in enumerate(idx[:-1]):
        prev_header = subheader
        subheader = df.iloc[i,1] if isinstance(df.iloc[i,0],float)  else df.iloc[i,0]
        df.loc[idx[j]:idx[j+1],col_name] = subheader if subheader != '' else prev_header
    # df.drop(idx,axis=0,inplace=True,errors='ignore') 
    return df

def _clean_qtr(
    file_path:str,
    regex_pattern = 'Affiliated\s+Investments:\s+\(\d+\)'
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0)
    df.replace(['\u200b','',')',':','$','%',0],np.nan,inplace=True) #':','$','%'
    df.dropna(axis=1,how='all',inplace=True)
    df.dropna(axis=0,how='all',inplace=True)
    
    cols = df.iloc[0].str.replace('[^a-zA-Z]', '', regex=True)
    aff_inv = df.apply(lambda row:row.astype(str).str.match(regex_pattern).all(),axis=1)
    if aff_inv.sum() > 0:
        df[aff_inv] = [df[aff_inv].iloc[0,0]] + [None]*(df.shape[1] - 1)
    if ((cols == '') + (cols == 'nan') + (cols == np.nan) + (cols == 'NaN')).sum() > int(file_path.split('\\')[-3] == '1396440'):
        df = df.apply(remove_row_duplicates, axis=1)
    else:
        df.columns = cols
    df = merge_duplicate_columns(df.reset_index(drop=True))
    if '2024-03-31' not in file_path:
        df.replace({None:np.nan,'':np.nan},inplace=True)
    if ((cols == '') + (cols == 'nan') + (cols == np.nan) + (cols == 'NaN')).sum() > int(file_path.split('\\')[-3] == '1396440') or\
        '\\'.join(file_path.split('\\')[-2:]) in ('2020-06-30\Schedule_of_Investments_2.csv','2020-06-30\Schedule_of_Investments_4.csv','2024-03-31\Schedule_of_Investments_4.csv',):
        df.dropna(axis=1,how='all',inplace=True)
        df.dropna(axis=0,how='all',inplace=True)
        
    df.drop(columns=df.columns[pd.isna(df.columns)].tolist() + [col for col in df.columns if col == ''],axis=1,inplace=True)
    return df


cik = 1490349
ROOT_PATH = r'C:\Users\pysol\Desktop\projects\sec_filings'

def main()->None:
    bdc = os.path.join(ROOT_PATH,str(cik))
    qtrs = os.listdir(bdc)
    for qtr in qtrs:
        if '.csv' in qtr or not os.path.exists(os.path.join(bdc,qtr,f'Schedule_of_Investments_0.csv')) or '2021-01-28' == qtr:
            continue
        # qtr = '2024-03-31'
        print(qtr)
        dfs = []
        index_list_sum = i = 0
        col = None
        while index_list_sum == 0:
            qtr_file = os.path.join(bdc,qtr,f'Schedule_of_Investments_{i}.csv')
            print(qtr_file)
            df = _clean_qtr(qtr_file)
            if i == 0:
                col = df.columns.tolist()
            else:
                df.columns = col
            dfs.append(df)
            index_list = df.apply(
                lambda row:row.astype(str).str.contains(stopping_criterion(), case=False, na=False).any(),
                axis=1
            )
            index_list_sum = index_list.sum()
            i += 1
        
        date_final = pd.concat(dfs,axis=0,ignore_index=True)#pd.DataFrame(concat(*dfs))
        date_final = extract_subheaders(date_final,control=True)
        date_final = extract_subheaders(date_final,control=False)

        date_final['qtr'] = qtr.split('\\')[-1]
        for i in range(3):
            date_final[date_final.columns[i]].fillna(method='ffill',inplace=True)
        if not os.path.exists(os.path.join(bdc,qtr,'output')):
            os.makedirs(os.path.join(bdc,qtr,'output'))
        date_final.to_csv(os.path.join(bdc,qtr,'output',f'{qtr}.csv'),index=False)
        # break
    
    # Use glob to find files
    files = sorted(glob.glob(f'{cik}/*/output/*.csv'), key=extract_date)
    single_truth = pd.concat([
        pd.read_csv(df) for df in files
    ],axis=0,ignore_index=True)
    single_truth.to_csv(os.path.join(str(cik),f'{cik}_soi_table.csv'),index=False)

import warnings

# Suppress future warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.filterwarnings('ignore', category=pd.errors.SettingWithCopyWarning)
main()


2011-03-31
C:\Users\pysol\Desktop\projects\sec_filings\1490349\2011-03-31\Schedule_of_Investments_0.csv
2011-06-30
C:\Users\pysol\Desktop\projects\sec_filings\1490349\2011-06-30\Schedule_of_Investments_0.csv
2011-09-30
C:\Users\pysol\Desktop\projects\sec_filings\1490349\2011-09-30\Schedule_of_Investments_0.csv
2011-12-31
C:\Users\pysol\Desktop\projects\sec_filings\1490349\2011-12-31\Schedule_of_Investments_0.csv
2012-03-31
C:\Users\pysol\Desktop\projects\sec_filings\1490349\2012-03-31\Schedule_of_Investments_0.csv
2012-06-30
C:\Users\pysol\Desktop\projects\sec_filings\1490349\2012-06-30\Schedule_of_Investments_0.csv
C:\Users\pysol\Desktop\projects\sec_filings\1490349\2012-06-30\Schedule_of_Investments_1.csv
2012-09-30
C:\Users\pysol\Desktop\projects\sec_filings\1490349\2012-09-30\Schedule_of_Investments_0.csv
2012-12-31
C:\Users\pysol\Desktop\projects\sec_filings\1490349\2012-12-31\Schedule_of_Investments_0.csv
2013-03-31
C:\Users\pysol\Desktop\projects\sec_filings\1490349\2013-03-31\S

In [78]:
def _clean_qtr(
    file_path:str,
    regex_pattern = 'Affiliated\s+Investments:\s+\(\d+\)'
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0)
    df.replace(['\u200b','',')',':','$','%',0],np.nan,inplace=True) #':','$','%'
    df.dropna(axis=1,how='all',inplace=True)
    df.dropna(axis=0,how='all',inplace=True)
    
    cols = df.iloc[0].str.replace('[^a-zA-Z]', '', regex=True)
    aff_inv = df.apply(lambda row:row.astype(str).str.match(regex_pattern).all(),axis=1)
    if aff_inv.sum() > 0:
        df[aff_inv] = [df[aff_inv].iloc[0,0]] + [None]*(df.shape[1] - 1)
    if ((cols == '') + (cols == 'nan') + (cols == np.nan) + (cols == 'NaN')).sum() > int(file_path.split('\\')[-3] == '1396440'):
        df = df.apply(remove_row_duplicates, axis=1)
    else:
        df.columns = cols
    df = merge_duplicate_columns(df.reset_index(drop=True))
    if '2024-03-31' not in file_path:
        df.replace({None:np.nan,'':np.nan},inplace=True)
    if ((cols == '') + (cols == 'nan') + (cols == np.nan) + (cols == 'NaN')).sum() > int(file_path.split('\\')[-3] == '1396440') or\
        '\\'.join(file_path.split('\\')[-2:]) in ('2020-06-30\Schedule_of_Investments_2.csv','2020-06-30\Schedule_of_Investments_4.csv','2024-03-31\Schedule_of_Investments_4.csv',):
        df.dropna(axis=1,how='all',inplace=True)
        df.dropna(axis=0,how='all',inplace=True)
        
    df.drop(columns=df.columns[pd.isna(df.columns)].tolist() + [col for col in df.columns if col == ''],axis=1,inplace=True)
    return df


file_path = r'C:\Users\pysol\Desktop\projects\sec_filings\1490349\2024-03-31\Schedule_of_Investments_4.csv'

# regex_pattern = 'Affiliated\s+Investments:\s+\(\d+\)'
# df = pd.read_csv(file_path, index_col=0)
# df.replace(['\u200b','',')',':','$','%',0],np.nan,inplace=True) #':','$','%'
# df.dropna(axis=1,how='all',inplace=True)
# df.dropna(axis=0,how='all',inplace=True)
# cols = df.iloc[0].str.replace('[^a-zA-Z]', '', regex=True)
# aff_inv = df.apply(lambda row:row.astype(str).str.match(regex_pattern).all(),axis=1)
# df[aff_inv] = [df[aff_inv].iloc[0]] + [None]*(df.shape[1] - 1)

# if ((cols == '') + (cols == 'nan') + (cols == np.nan) + (cols == 'NaN')).sum() > int(file_path.split('\\')[-3] == '1396440'):
#     df = df.apply(remove_row_duplicates, axis=1)
# else:
#     df.columns = cols
    
# df.columns = cols
# df = merge_duplicate_columns(df.reset_index(drop=True))
# print(df.shape)


# df.replace({'\u200b': np.nan, '': np.nan, ')': np.nan, ':': np.nan, '$': np.nan, '%': np.nan}, inplace=True)

df = _clean_qtr(file_path)
df

Affiliated  Investments:  (6)


0                                            Company                 Industry  \
0                                       Company  (1)                 Industry   
1  0     Affiliated  Investments:  (6)
1     Affi...                     None   
2                       Black Angus Steakhouses, LLC  Hotel, Gaming & Leisure   
3                                                NaN                      NaN   
4                                                NaN                      NaN   
5                                                NaN                      NaN   
6                                                NaN                      NaN   
7                           FST Holdings Parent, LLC     High Tech Industries   
8                                                NaN                      NaN   
9                   Subtotal  Affiliated Investments                      NaN   

0                                   TypeofInvestment   Maturity  \
0                                Type of  Investment   Maturity   
1                                               None       None   
2  Senior Secured First Lien Delayed Draw Term Lo...  1/31/2025   
3  Senior Secured First Lien Term Loan (SOFR + CS...  1/31/2025   
4  Senior Secured First Lien Super Priority Delay...  1/31/2025   
5         Equity -  17.92  % Membership Interest(21)        NaN   
6                                                NaN        NaN   
7                   Equity -  625,548  Class A Units        NaN   
8                                                NaN        NaN   
9                                                NaN        NaN   

0            ParAmountSharesUnits         AmortizedCost         FairValue  \
0  Par Amount/  Shares/Units  (2)  Amortized  Cost  (3)  Fair  Value  (4)   
1                                                                           
2                          908080                875749            875749   
3                        13513874               7767533            810832   
4                         1991878               1920960           1920960   
5                               -                     -                 -   
6                        16413832              10564242           3607541   
7                          625548              10000000          10726326   
8                          625548              10000000          10726326   
9                        17039380              20564242          14333867   

0             ofNetAssets  
0  % of  Net  Assets  (5)  
1                          
2                    0.57  
3                    0.53  
4                    1.25  
5                    0.00  
6                    2.35  
7                    6.95  
8                    6.95  
9                    9.30

In [34]:
df.columns[0] == np.nan

False

## cik==1379785

In [28]:
import os
import re
import glob
import datetime
import pandas as pd
import numpy as np


def stopping_criterion(
    search_string:str='total investments'
)->str:
    # Regular expression to ignore whitespace and case
    regex_pattern = search_string.replace(' ', r'\s*')
    return '{}|{}'.format(regex_pattern,'Invesmtents')

def concat(*dfs)->list:
    final = []
    for df in dfs:
        final.extend(df.values.tolist())
    return final

def common_subheaders()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        ('senior secured loans',
        'first lien',
        'second lien',
        'senior secured bonds',
        'subordinated debt',
        'equity/other',
        'collateralized securities',
        'preferred equity—',
        'Equity/Warrants',
        'unsecured debt',
        'senior secured notes',
        'warrants',
        'total senior secured first lien term loans')
    ))

def standard_field_names()->tuple:
    return (
        'portfolio',
        'footnotes',
        'industry',
        'rate',
        'floor',
        'maturity',
        'principal amount', # TODO change stand names for more dynamic fuzzywuzzy matching
        'cost',
        'value',
        'investment',
        'date',
        'subheaders',
        'number of shares'
    )

def company_control_headers()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        (
        'control investments',
        'affiliate investments',
        'non-control/non-affilate investments',
        'Non-Controlled/Non-Affiliated  Investments:',
        'Affiliated  Investments:',
        'Non-Controlled/Non-Affiliated  Investments  :',
        'Affiliated  Investments  :',
        'Non-controlled/Non-affiliated Investments',
        'Affiliated Investments',
        )
    ))

# Function to extract date and convert to datetime object
def extract_date(file_path):
    # Extract date from file path (assuming date is always in 'YYYY-MM-DD' format)
    date_str = re.search(r'\d{4}-\d{2}-\d{2}', file_path).group()
    return datetime.datetime.strptime(date_str, '%Y-%m-%d')

def remove_row_duplicates(row):
    seen = set()
    return pd.Series([x if x not in seen and not seen.add(x) else None for x in row])

def shift_part(row,left,after=3):
    # Keeping the first three values unchanged
    first_part = row[:after]
    # Shifting the remaining part of the row to the left by 1
    shifted_part = row[after:].shift(-1 if left else 1)
    # Concatenating the two parts
    return pd.concat([first_part, shifted_part])



def merge_duplicate_columns(
    df:pd.DataFrame,
)->pd.DataFrame:
    duplicate_cols = df.columns[df.columns.duplicated(keep=False)]
    for col_name in duplicate_cols.unique():
        duplicate_data = df.loc[:, df.columns == col_name]
        merged_data = duplicate_data.apply(lambda row: ' '.join(set(row.dropna().astype(str))), axis=1)
        df = df.loc[:, df.columns != col_name]
        df[col_name] = merged_data
    return df

def extract_subheaders(
    df:pd.DataFrame,
    control:bool,
)->pd.DataFrame:
    col_name = 'company_control' if control else 'TypeofInvestment'
    if col_name in df.columns:
        return df
    include = df.apply(
        lambda row: re.search('|'.join(company_control_headers() if control else common_subheaders()), str(row[0]), re.IGNORECASE) is not None,
        axis=1
    )  
    
    exclude = ~df.apply(
        lambda row: row.astype(str).str.contains('total', case=False, na=False).any(),
        axis=1
    )
    idx = df[include & exclude].index.tolist()
    df[col_name] = None
    if not idx:
        return df

    prev_header = subheader = None
    df.loc[idx[-1]:,col_name] = df.iloc[idx[-1],1] if isinstance(df.iloc[idx[-1],0],float)  else df.iloc[idx[-1],0]
    for j,i in enumerate(idx[:-1]):
        prev_header = subheader
        subheader = df.iloc[i,1] if isinstance(df.iloc[i,0],float)  else df.iloc[i,0]
        df.loc[idx[j]:idx[j+1],col_name] = subheader if subheader != '' else prev_header
    # df.drop(idx,axis=0,inplace=True,errors='ignore') 
    return df


def clean_bbdc(
    file_path:str
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0)
    df.dropna(axis=1,how='all',inplace=True)
    df.dropna(axis=0,how='all',inplace=True)
    df.replace(['\u200b','%',],np.nan,inplace=True) #':','$','%'

    if not '2012-06-30' in file_path:
        df[df.apply(lambda row: row.astype(str).str.contains('TRIANGLE CAPITAL CORPORATION').any(), axis=1)] = ''
        regex_pattern = '|'.join(map(re.escape, standard_field_names()))
        mask = df.iloc[:,0].str.contains(regex_pattern, case=False, na=False)
        df.iloc[0] = df.iloc[:mask.idxmax()].astype(str).agg(' '.join)
        df.reset_index(drop=True,inplace=True)
        df.drop(axis=0, index=1,inplace=True)

    for i in range(df.shape[0]):
        df.iloc[i] = [np.nan if  item in ['None None','nan nan'] else str(item).replace('nan','').replace('None','') for item in df.iloc[i]]
        
    if '2010-09-30/Schedule_of_Investments_0.csv' in file_path:
        df.iloc[0] = shift_part(df.iloc[0],left=True)
    if '2010-09-30/Schedule_of_Investments_1.csv' in file_path:
        df.iloc[0] = shift_part(df.iloc[0],left=False,after=8)

        
    df.columns = df.iloc[0].astype(str)
    df = merge_duplicate_columns(df)
    df = df.apply(remove_row_duplicates, axis=1)
    non_empty_counts = df.applymap(lambda x: x != '' and pd.notna(x)).sum()
    return df.loc[:, non_empty_counts > 3]

cik = 1379785
ROOT_PATH = r'C:\Users\pysol\Desktop\projects\sec_filings'

def main()->None:
    bdc = os.path.join(ROOT_PATH,str(cik))
    qtrs = os.listdir(bdc)
    for qtr in qtrs:
        if '.csv' in qtr or not os.path.exists(os.path.join(bdc,qtr,f'Schedule_of_Investments_0.csv')):
            continue
        dfs = []
        index_list_sum = i = 0
        qtr = '2010-09-30'
        while index_list_sum == 0:
            qtr_file = os.path.join(bdc,qtr,f'Schedule_of_Investments_{i}.csv')
            df = clean_bbdc(qtr_file)
            dfs.append(df)
            index_list = df.apply(
                lambda row:row.astype(str).str.contains(stopping_criterion(), case=False, na=False).any(),
                axis=1
            )
            index_list_sum = index_list.sum()
            i += 1
        
        date_final = pd.DataFrame(concat(*dfs))
        date_final = extract_subheaders(date_final,control=True)

        date_final['qtr'] = qtr.split('\\')[-1]
        for i in range(3):
            date_final[date_final.columns[i]].fillna(method='ffill',inplace=True)
        if not os.path.exists(os.path.join(bdc,qtr,'output')):
            os.makedirs(os.path.join(bdc,qtr,'output'))
        date_final.to_csv(os.path.join(bdc,qtr,'output',f'{qtr}.csv'),index=False)
        break
    # Use glob to find files
    files = sorted(glob.glob(f'{cik}/*/output/*.csv'), key=extract_date)
    single_truth = pd.concat([
        pd.read_csv(df) for df in files
    ],axis=0,ignore_index=True)
    single_truth.to_csv(os.path.join(str(cik),f'{cik}_soi_table.csv'),index=False)
    
import warnings

# Suppress future warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.filterwarnings('ignore', category=pd.errors.SettingWithCopyWarning)
# main()

In [106]:

# string_fields = (        
#     'portfolio_company',
#     # 'industry',
#     'type_of_investment',
# )

def divide_evenly(number, parts):
    if parts <= 0:
        raise ValueError("Number of parts must be greater than 0.")
    if number < 0:
        raise ValueError("Number must be non-negative.")
        
    base_part = number // parts
    extra_needed = number % parts
    
    # Parts that get an extra unit to handle the remainder
    parts_with_extra = [base_part + 1] * extra_needed
    # Parts that don't get the extra unit
    parts_without_extra = [base_part] * (parts - extra_needed)
    
    # Concatenate the two parts
    result = parts_with_extra + parts_without_extra
    
    return result


# Function to attempt conversion and determine type
def tag_column_name(
    df:pd.DataFrame,
    numeric_fields:tuple=('principal_amount','cost','fair_value',)
)->str:
    
    numeric_cols = [
        df.loc[1:,col].str.isnumeric().any() or df.loc[1:,col].isna().all()
        for col in df.columns
    ]
    # Separating the DataFrame into two based on the type of columns
    df_numeric,df_non_numeric = df.loc[:,numeric_cols],df.loc[:,[not value for value in numeric_cols]]
    # numeric_fields = df_numeric.iloc[0][df_numeric.iloc[0].notna()].tolist()
    string_fields = df_non_numeric.iloc[0][df_non_numeric.iloc[0].notna()].tolist()
    string_fields.remove('Industry')
    # num_div = divide_evenly(df_numeric.shape[1],  len(numeric_fields))
    num_div = round(df_numeric.shape[1] /  len(numeric_fields))
    print(numeric_fields,string_fields,num_div,df_numeric.shape[1],  len(numeric_fields))
        
    # numeric_mask = df_numeric.applymap(lambda x: x != '' and pd.notna(x)).sum()
    # string_mask = df_non_numeric.applymap(lambda x: x != '' and pd.notna(x)).sum()
    # df_numeric,df_non_numeric = df_numeric.loc[:,numeric_mask > 1],df_non_numeric.loc[:,string_mask > 1]
    
    i,num_cols = 0,[None]*df_numeric.shape[1]
    start,end = i*num_div,min((i + 1)*num_div,df_numeric.shape[1])
    while i*len(numeric_fields) - df_numeric.shape[1] and start < end:
        num_cols[start:end] = [numeric_fields[i]]*(end - start)
        i += 1
        start,end = i*num_div,min((i + 1)*num_div,df_numeric.shape[1])
    df_numeric.columns = num_cols
    
    flag,itr,columns = False,0,[None]*len(df_non_numeric.columns)
    for i,col in enumerate(df_non_numeric.columns):
        flag = df_non_numeric.loc[:,col].str.contains('%/*()',regex=True).any()
        columns[i] = string_fields[itr]
        if not flag:
            columns[i] = 'industry'
            itr = int(not flag)
    df_non_numeric.columns = columns
                
    return pd.concat([df_non_numeric,df_numeric],axis=1)
        


tag_column_name(df)


('principal_amount', 'cost', 'fair_value') ['PortfolioCompany', 'TypeofInvestment(1)(2)', 'PrincipalAmount'] 3 8 3


C:\Users\pysol\AppData\Local\Temp\ipykernel_25236\864796125.py:60: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  flag = df_non_numeric.loc[:,col].str.contains('%/*()',regex=True).any()


PortfolioCompany  \
0                               PortfolioCompany   
1                           MediaTempleInc.(7%)*   
2                                            NaN   
3                                            NaN   
4                                            NaN   
5                    MincoTechnologyLabsLLC(3%)*   
6                                            NaN   
7                                            NaN   
8                  NovolyteTechnologiesInc.(5%)*   
9                                            NaN   
10                                           NaN   
11                                           NaN   
12                       SyrgisHoldingsInc.(2%)*   
13                                           NaN   
14                                           NaN   
15               TBGAnesthesiaManagementLLC(4%)*   
16                                           NaN   
17                                           NaN   
18              TrustHouseServicesGroupInc.(3%)*   
19                                           NaN   
20                                           NaN   
21                                           NaN   
22  TulsaInspectionResourcesInc.(“TIR”)andRegent   
23                   TIRPartnersLLC(“RTIR”)(3%)*   
24                                           NaN   
25                                           NaN   
26                                           NaN   
27               Twin-StarInternationalInc.(3%)*   
28                                           NaN   
29                                           NaN   

                               industry  \
0                              Industry   
1                    WebHostingServices   
2                                   NaN   
3                                   NaN   
4                                   NaN   
5             SemiconductorDistribution   
6                                   NaN   
7                                   NaN   
8                SpecialtyManufacturing   
9                                   NaN   
10                                  NaN   
11                                  NaN   
12        SpecialtyChemicalManufacturer   
13                                  NaN   
14                                  NaN   
15          PhysicianManagementServices   
16                                  NaN   
17                                  NaN   
18               FoodManagementServices   
19                                  NaN   
20                                  NaN   
21                                  NaN   
22           PipelineInspectionServices   
23                                  NaN   
24                                  NaN   
25                                  NaN   
26                                  NaN   
27  ConsumerHomeFurnishingsManufacturer   
28                                  NaN   
29                                  NaN   

                         TypeofInvestment(1)(2)  \
0                        TypeofInvestment(1)(2)   
1        SubordinatedNote(12%Cash4%PIKDue04/15)   
2                                           NaN   
3                                           NaN   
4                                           NaN   
5     SubordinatedNote(13%Cash3.25%PIKDue05/16)   
6                                           NaN   
7                                           NaN   
8      SubordinatedNote(12%Cash5.5%PIKDue04/15)   
9                                           NaN   
10                                          NaN   
11                                          NaN   
12  SeniorNotes(7.75%-10.75%CashDue08/12-02/14)   
13                                          NaN   
14                                          NaN   
15                  SeniorNote(14%CashDue11/14)   
16                                          NaN   
17                                          NaN   
18       SubordinatedNote(12%Cash2%PIKDue09/15)   
19                                          NaN   
20            

In [100]:

def divide_evenly(number, parts):
    if parts <= 0:
        raise ValueError("Number of parts must be greater than 0.")
    if number < 0:
        raise ValueError("Number must be non-negative.")
        
    base_part = number // parts
    extra_needed = number % parts
    
    # Parts that get an extra unit to handle the remainder
    parts_with_extra = [base_part + 1] * extra_needed
    # Parts that don't get the extra unit
    parts_without_extra = [base_part] * (parts - extra_needed)
    
    # Concatenate the two parts
    result = parts_with_extra + parts_without_extra
    
    return result

divide_evenly(8,3)

[3, 3, 2]

## SEC API

In [1]:
from sec_api import ExtractorApi

api_key = 'ad73111c598021aa3c07419e067f727ae15d4427e8b6645af4ff83a83213d5b5'
extractorApi = ExtractorApi(api_key)

test_qtr = 'https://www.sec.gov/Archives/edgar/data/0001379785/000119312512101223/d310549d10k.htm'
help(extractorApi)

Help on ExtractorApi in module sec_api.index object:

class ExtractorApi(builtins.object)
 |  ExtractorApi(api_key, proxies=None)
 |  
 |  Base class for 10-K/10-Q/8-K item/section extractor API
 |  
 |  Methods defined here:
 |  
 |  __init__(self, api_key, proxies=None)
 |      Initialize self.  See help(type(self)) for accurate signature.
 |  
 |  get_section(self, filing_url='', section='1A', return_type='text')
 |  
 |  ----------------------------------------------------------------------
 |  Data descriptors defined here:
 |  
 |  __dict__
 |      dictionary for instance variables (if defined)
 |  
 |  __weakref__
 |      list of weak references to the object (if defined)



In [7]:
test = extractorApi.get_section(
    filing_url=test_qtr, 
    section="1", 
    return_type="text",
)
print(test)

 Item 1. Business. 

We are a Maryland corporation incorporated on October 10, 2006, for the purposes of acquiring 100% of the equity interests in Triangle Mezzanine Fund LLLP (&#147;Triangle SBIC&#148;) and its general partner, Triangle Mezzanine LLC (&#147;TML&#148;), raising capital in our initial public offering, which was completed in February 2007 (the &#147;IPO&#148;) and thereafter operating as an internally managed business development company (&#147;BDC&#148;) under the Investment Company Act of 1940 (the &#147;1940 Act&#148;). On December 15, 2009, Triangle Mezzanine Fund II, LP (&#147;Triangle SBIC II&#148;) was organized as a limited partnership under the laws of the State of Delaware. Triangle SBIC&#146;s Small Business Investment Company (&#147;SBIC&#148;) license from the United States Small Business Administration (the &#147;SBA&#148;) became effective on September 11, 2003 and Triangle SBIC II&#146;s SBIC license became effective on May 26, 2010. Unless otherwise note

In [15]:
from sec_api import FullTextSearchApi

fullTextSearchApi = FullTextSearchApi(api_key=api_key)
query = {
  "query": '"LPCN 1154"',
  "formTypes": ['8-K', '10-Q'],
  "startDate": '2021-01-01',
  "endDate": '2021-06-14',
}
filings = fullTextSearchApi.get_filings(query)
filings

{'total': {'value': 3, 'relation': 'eq'},
 'filings': [{'accessionNo': '0001104659-21-080527',
   'cik': '1535955',
   'companyNameLong': 'Lipocine Inc. (LPCN) (CIK 0001535955)',
   'ticker': 'LPCN',
   'description': 'EXHIBIT 99.1',
   'formType': '8-K',
   'type': 'EX-99.1',
   'filingUrl': 'https://www.sec.gov/Archives/edgar/data/1535955/000110465921080527/tm2119438d1_ex99-1.htm',
   'filedAt': '2021-06-14'},
  {'accessionNo': '0001104659-21-080525',
   'cik': '1535955',
   'companyNameLong': 'Lipocine Inc. (LPCN) (CIK 0001535955)',
   'ticker': 'LPCN',
   'description': 'EXHIBIT 99.1',
   'formType': '8-K',
   'type': 'EX-99.1',
   'filingUrl': 'https://www.sec.gov/Archives/edgar/data/1535955/000110465921080525/tm2119156d1_ex99-1.htm',
   'filedAt': '2021-06-14'},
  {'accessionNo': '0001104659-21-080527',
   'cik': '1535955',
   'companyNameLong': 'Lipocine Inc. (LPCN) (CIK 0001535955)',
   'ticker': 'LPCN',
   'description': 'FORM 8-K',
   'formType': '8-K',
   'type': '8-K',
   '

## cik == 1490927

In [73]:
import os
import re
import glob
import datetime
import pandas as pd
import numpy as np
from fuzzywuzzy import process

def get_standard_name(col, choices, score_cutoff=60):
    best_match, score = process.extractOne(col, choices)
    if score > score_cutoff:
        return best_match
    return col

def stopping_criterion(
    search_string:str='total investments'
)->str:
    # Regular expression to ignore whitespace and case
    regex_pattern = search_string.replace(' ', r'\s*')
    return '{}|{}|{}|{}'.format(regex_pattern,'Invesmtents',r'130.4%\s*(b)',r'178.1%\s*(b)',r'Total\s*Control\s*&\s*Affiliate\s*Investments')

def concat(*dfs)->list:
    final = []
    for df in dfs:
        final.extend(df.values.tolist())
    return final

def common_subheaders()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        ('senior secured loans',
        'first lien',
        'second lien',
        'senior secured bonds',
        'subordinated debt',
        'equity/other',
        'collateralized securities',
        'preferred equity—',
        'Equity/Warrants',
        'unsecured debt',
        'senior secured notes',
        'warrants',
        'total senior secured first lien term loans',
        'Secured Debt')
    ))

def standard_field_names()->tuple:
    return (
        'portfolio',
        'footnotes',
        'industry',
        'rate',
        'floor',
        'maturity',
        'principal amount', # TODO change stand names for more dynamic fuzzywuzzy matching
        'cost',
        'value',
        'investment',
        'date',
        'subheaders',
        'number of shares',
        'of net assets',
        'type of investment',
        'effective yield'
    )

def company_control_headers()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        (
        'control investments',
        'affiliate investments',
        'non-control/non-affilate investments',
        'Non-Controlled/Non-Affiliated  Investments:',
        'Affiliated  Investments:',
        'Non-Controlled/Non-Affiliated  Investments  :',
        'Affiliated  Investments  :',
        'Non-controlled/Non-affiliated Investments',
        'Affiliated Investments',
        )
    ))

def strip_string(
    columns_names:list,
    standardize:bool=False
)->tuple:
    columns = tuple(map(lambda col:re.sub(r'[^a-z]', '', str(col).lower()),columns_names))
    if standardize:
        standard_fields = standard_field_names()
        return tuple(
            get_standard_name(col,standard_fields) for col in columns
        )
    return columns

def get_key_fields(
    df_cur:pd.DataFrame
)->tuple:
    important_fields = standard_field_names() + common_subheaders()
    for idx,row in enumerate(df_cur.iterrows()):
        found = any(any(
            key in str(field).lower() 
            for key in important_fields)
                    for field in row[-1].dropna().tolist()
            )
        if found and len(set(row[-1].dropna().tolist())) >= 5:
            fields = strip_string(row[-1].tolist(),standardize=found) ,idx
            return fields
    return strip_string(df_cur.iloc[0].tolist(),standardize=found),0

# Function to extract date and convert to datetime object
def extract_date(file_path):
    # Extract date from file path (assuming date is always in 'YYYY-MM-DD' format)
    date_str = re.search(r'\d{4}-\d{2}-\d{2}', file_path).group()
    return datetime.datetime.strptime(date_str, '%Y-%m-%d')

def remove_row_duplicates(row):
    seen = set()
    return pd.Series([x if x not in seen and not seen.add(x) else None for x in row])


def merge_duplicate_columns(
    df:pd.DataFrame,
)->pd.DataFrame:
    duplicate_cols = df.columns[df.columns.duplicated(keep=False)]
    for col_name in duplicate_cols.unique():
        duplicate_data = df.loc[:, df.columns == col_name]
        merged_data = duplicate_data.apply(lambda row: ' '.join(set(row.dropna().astype(str))), axis=1)
        df = df.loc[:, df.columns != col_name]
        df[col_name] = merged_data
    return df

def extract_subheaders(
    df:pd.DataFrame,
    control:bool,
)->pd.DataFrame:
    col_name = 'company_control' if control else 'TypeofInvestment'
    if col_name in df.columns:
        return df
    include = df.apply(
        lambda row: re.search('|'.join(company_control_headers() if control else common_subheaders()), str(row[0]), re.IGNORECASE) is not None,
        axis=1
    )  
    
    exclude = ~df.apply(
        lambda row: row.astype(str).str.contains('total|Inc|Ltd|LLC|Holdings|LP|Co|Corporation', case=False, na=False).any(),
        axis=1
    )
    idx = df[include & exclude].index.tolist()
    df[col_name] = None
    if not idx:
        return df

    prev_header = subheader = None
    df.loc[idx[-1]:,col_name] = df.iloc[idx[-1],1] if isinstance(df.iloc[idx[-1],0],float)  else df.iloc[idx[-1],0]
    for j,i in enumerate(idx[:-1]):
        prev_header = subheader
        subheader = df.iloc[i,1] if isinstance(df.iloc[i,0],float)  else df.iloc[i,0]
        df.loc[idx[j]:idx[j+1],col_name] = subheader if subheader != '' else prev_header
    # df.drop(idx,axis=0,inplace=True,errors='ignore') 
    return df

def _clean(
    file_path:str,
    regex_pattern:str=r'\w+\s+\d{1,2},\s+\d{4}'
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0)
    df.dropna(axis=0,how='all',inplace=True)
    df = df[~df.apply(lambda row:row.str.match(regex_pattern).all(),axis=1)]

    if '2013-06-30\Schedule_of_Investments_1.csv' in file_path:
        df = df.iloc[:,[0,2,4,6,10,14,18]]
        df.columns = list(range(df.shape[1]))
        return df
    elif '2013-06-30\Schedule_of_Investments_2.csv' in file_path:
        df = df.iloc[:,[0,2,4,7,11,15,18]]
        df.columns = list(range(df.shape[1]))
        return df
    elif '2011-12-31\Schedule_of_Investments_1.csv' in file_path:
        df = df.iloc[:,[0,2,4,6,10,14,18,21]]
        df.columns = list(range(df.shape[1]))
        return df
    elif '2011-12-31\Schedule_of_Investments_1.csv' in file_path:
        df = df.iloc[:,[0,2,4,6,9,12,15,18]]
        df.columns = list(range(df.shape[1]))
        return df
    elif '2012-03-31\Schedule_of_Investments_1.csv' in file_path:
        df = df.iloc[:,[0,2,4,6,10,14,18,21]]
        df.columns = list(range(df.shape[1]))
        return df
    elif '2012-12-31\Schedule_of_Investments_1.csv' in file_path:
        df = df.iloc[:,[0,2,4,6,9,12,15,18]]
        df.columns = list(range(df.shape[1]))
        return df
    elif '2013-03-31\Schedule_of_Investments_1.csv' in file_path:
        df = df.iloc[:,[0,2,4,6,10,14,18,21]]
        df.columns = list(range(df.shape[1]))
        return df
    
    important_fields,idx = get_key_fields(df)
    df.columns = important_fields
    df = merge_duplicate_columns(df)
    df.replace([' '],'_',inplace=True)
    df.replace(['\u200b','','%','nan'],np.nan,inplace=True) #':','$','%'
    # df.columns = list(range(df.shape[1]))
    columns = (~df.isna()).sum(axis=0) <= 1
    df.drop(columns=columns[columns].index,inplace=True)
    duplicate_idx = df.apply(lambda row:row.duplicated().sum() > 3,axis=1)
    df.loc[duplicate_idx] = df.loc[duplicate_idx].apply(remove_row_duplicates, axis=1)
    return df.reset_index(drop=True)

cik = 1490927
ROOT_PATH = r'C:\Users\pysol\Desktop\projects\sec_filings'

def main()->None:
    bdc = os.path.join(ROOT_PATH,str(cik))
    qtrs = os.listdir(bdc)
    for qtr in qtrs:
        if '.csv' in qtr or not os.path.exists(os.path.join(bdc,qtr,f'Schedule_of_Investments_0.csv')):
            continue
        # qtr = '2013-06-30'
        index_list_sum = i = 0
        df = _clean(os.path.join(bdc,qtr,f'Schedule_of_Investments_{i}.csv'))
        index_list = df.apply(
            lambda row:row.astype(str).str.contains(stopping_criterion(), case=False, na=False).any(),
            axis=1
        )
        index_list_sum = index_list.sum()
        dfs = [df]     
        i += 1
        cols = df.columns.tolist()
        while index_list_sum == 0 :
            df = _clean(os.path.join(bdc,qtr,f'Schedule_of_Investments_{i}.csv'))
            if set(list(range(10))) >= set(df.columns.tolist()):
                df.columns = cols
            dfs.append(df)
            index_list = df.apply(
                lambda row:row.astype(str).str.contains(stopping_criterion(), case=False, na=False).any(),
                axis=1
            )
            index_list_sum = index_list.sum()
            i += 1
            
        date_final = dfs[0]
        if len(dfs) > 1:
            date_final = pd.concat(dfs,axis=0,ignore_index=True)#pd.DataFrame(concat(*dfs))
        date_final = extract_subheaders(date_final,control=True)
        date_final = extract_subheaders(date_final,control=False)

        date_final['qtr'] = qtr.split('\\')[-1]
        if not os.path.exists(os.path.join(bdc,qtr,'output')):
            os.makedirs(os.path.join(bdc,qtr,'output'))
        columns_to_drop = date_final.notna().sum() <= 2
        date_final.drop(columns=columns_to_drop[columns_to_drop].index)
        date_final.to_csv(os.path.join(bdc,qtr,'output',f'{qtr}.csv'),index=False)
        # break
    # Use glob to find files
    files = sorted(glob.glob(f'{cik}/*/output/*.csv'), key=extract_date)
    single_truth = pd.concat([
        pd.read_csv(df) for df in files
    ],axis=0,ignore_index=True)
    single_truth.to_csv(os.path.join(str(cik),f'{cik}_soi_table.csv'),index=False)
    
    
import warnings

# Suppress future warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.filterwarnings('ignore', category=pd.errors.SettingWithCopyWarning)
main()

C:\Users\pysol\AppData\Local\Temp\ipykernel_3608\1531911120.py:222: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stopping_criterion(), case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_3608\1531911120.py:222: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stopping_criterion(), case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_3608\1531911120.py:222: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stopping_criterion(), case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_3608\1531911120.py:222: UserWarning: This pattern is interpreted as a regu

In [68]:
def _clean(
    file_path:str,
    regex_pattern:str=r'\w+\s+\d{1,2},\s+\d{4}'
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0)
    df.dropna(axis=0,how='all',inplace=True)
    df = df[~df.apply(lambda row:row.str.match(regex_pattern).all(),axis=1)]

    if '2013-06-30\Schedule_of_Investments_1.csv' in file_path:
        df = df.iloc[:,[0,2,4,6,10,14,18]]
        df.columns = list(range(df.shape[1]))
        return df
    elif '2013-06-30\Schedule_of_Investments_2.csv' in file_path:
        df = df.iloc[:,[0,2,4,7,11,15,18]]
        df.columns = list(range(df.shape[1]))
        return df
    elif '2011-12-31\Schedule_of_Investments_1.csv' in file_path:
        df = df.iloc[:,[0,2,4,6,10,14,18,21]]
        df.columns = list(range(df.shape[1]))
        return df
    elif '2011-12-31\Schedule_of_Investments_1.csv' in file_path:
        df = df.iloc[:,[0,2,4,6,9,12,15,18]]
        df.columns = list(range(df.shape[1]))
        return df
    elif '2012-03-31\Schedule_of_Investments_1.csv' in file_path:
        df = df.iloc[:,[0,2,4,6,10,14,18,21]]
        df.columns = list(range(df.shape[1]))
        return df
    elif '2012-12-31\Schedule_of_Investments_1.csv' in file_path:
        df = df.iloc[:,[0,2,4,6,9,12,15,18]]
        df.columns = list(range(df.shape[1]))
        return df
    elif '2013-03-31\Schedule_of_Investments_1.csv' in file_path:
        df = df.iloc[:,[0,2,4,6,10,14,18,21]]
        df.columns = list(range(df.shape[1]))
        return df
    
    important_fields,idx = get_key_fields(df)
    df.columns = important_fields
    df = merge_duplicate_columns(df)
    df.replace([' '],'_',inplace=True)
    df.replace(['\u200b','','%','nan'],np.nan,inplace=True) #':','$','%'
    # df.columns = list(range(df.shape[1]))
    columns = (~df.isna()).sum(axis=0) <= 1
    df.drop(columns=columns[columns].index,inplace=True)
    duplicate_idx = df.apply(lambda row:row.duplicated().sum() > 3,axis=1)
    df.loc[duplicate_idx] = df.loc[duplicate_idx].apply(remove_row_duplicates, axis=1)
    return df.reset_index(drop=True)

cols = ['portfolio', 'industry', 'rate', 'number of shares', 'cost', 'value', 'ofnetassets']
file_path = r'C:\Users\pysol\Desktop\projects\sec_filings\1490927\2013-03-31\Schedule_of_Investments_1.csv'
df = _clean(file_path)
# df.columns = cols
df

0  \
2         Senior Secured Second Lien Debt - 11.7% (b)   
3                         Eureka Hunter Holdings, LLC   
4                       Linc Energy Finance USA, Inc.   
5                                         MBLOX, Inc.   
6                               Teleflex Marine, Inc.   
7           Sub Total Senior Secured Second Lien Debt   
9                       Subordinated Debt - 16.5% (b)   
10                                         Gold, Inc.   
11                       S.B Restaurant Co., Inc. (d)   
12                               The SAVO Group, Ltd.   
13  Varel International Energy Mezzanine Funding C...   
14                          Vestcom Acquisition, Inc.   
15                        Sub Total Subordinated Debt   
17               Collateralized Securities - 3.7% (b)   
18             ALM 2012-6A CLO Subordinated Notes (e)   
19        Carlyle CGMS 2012-1A Subordinated Notes (e)   
20        Carlyle CGMS 2012-2A Subordinated Notes (e)   
21          MC Funding 2006 -1 Subordinated Notes (e)   
22                Sub Total Collateralized Securities   
24                            Equity/Other - 5.8% (b)   
25  PennantPark Credit Opportunities Fund, L.P. (f...   
26  Precision Dermatology, Inc., Warrants, Strike:...   
27  S.B Restaurant Co., Inc. - Warrants, Strike: $...   
28             Tennenbaum Waterman Fund, L.P. (f) (g)   
29            THL Credit Greenway Fund II LLC (f) (i)   
30                             Sub Total Equity/Other   
31                      TOTAL INVESTMENTS - 84.4% (b)   

                                            1                   2      3  \
2                                         NaN                 NaN    NaN   
3                           Energy: Oil & Gas   12.50%, 8/16/2018  13.07   
4                           Energy: Oil & Gas  12.50%, 10/31/2017  13.01   
5                          Telecommunications    10.75%, 9/1/2017  11.45   
6                     Hotel, Gaming & Leisure   13.50%, 8/24/2017  14.14   
7                                         NaN                 NaN    NaN   
9                                         NaN                 NaN    NaN   
10                Consumer Goods: Non-Durable  15.00%, 12/31/2017  16.54   
11                   Beverage, Food & Tobacco   14.00%, 1/10/2018  15.42   
12                       High Tech Industries   10.95%, 3/28/2017  11.11   
13                          Energy: Oil & Gas   14.00%, 6/12/2017  15.10   
14  Media: Advertising, Printing & Publishing   12.00%, 6/26/2019  12.80   
15                                        NaN                 NaN    NaN   
17                                        NaN                 NaN    NaN   
18  Banking, Finance, Insurance & Real Estate           6/14/2023  22.65   
19  Banking, Finance, Insurance & Real Estate           4/20/2022  27.18   
20  Banking, Finance, Insurance & Real Estate           7/20/2023  25.66   
21  Banking, Finance, Insurance & Real Estate          12/20/2020  23.28   
22                                        NaN                 NaN    NaN   
24                                        NaN                 NaN    NaN   
25  Banking, Finance, Insurance & Real Estate                 NaN    NaN   
26               Healthcare & Pharmaceuticals                 NaN    NaN   
27                   Beverage, Food & Tobacco                 NaN    NaN   
28  Banking, Finance, Insurance & Real Estate                 NaN    NaN   
29  Banking, Finance, Insurance & Real Estate                 NaN    NaN   
30                                        NaN                 NaN    NaN   
31                                        NaN                 NaN    NaN   

        4       5       6     7  
2     NaN     NaN     NaN   NaN  
3    5000    5000    4982   2.4  
4    9000    8845    9945   4.6  
5    7000    6966    6965   3.2  
6    3332    3263    3299   1.5  
7     NaN   24074   25191  11.7  
9     NaN     NaN     NaN   NaN  
10  12000   11761   11760   5.4  
11   4019    3937   

# cik == 1418076

In [18]:
import os
import re
import glob
import datetime
import pandas as pd
import numpy as np
from fuzzywuzzy import process

def get_standard_name(col, choices, score_cutoff=60):
    best_match, score = process.extractOne(col, choices)
    if score > score_cutoff:
        return best_match
    return col

def stopping_criterion()->str:
    return '{}'.format(r'Total\s*Investments')

def concat(*dfs)->list:
    final = []
    for df in dfs:
        final.extend(df.values.tolist())
    return final

def remove_row_duplicates(row:str)->pd.Series:
    seen = set()
    return pd.Series([x if x not in seen and not seen.add(x) else None for x in row])

def common_subheaders()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        ('senior secured loans',
        'first lien',
        'second lien',
        'senior secured bonds',
        'subordinated debt',
        'equity/other',
        'collateralized securities',
        'preferred equity—',
        'Equity/Warrants',
        'unsecured debt',
        'senior secured notes',
        'warrants',
        'total senior secured first lien term loans',
        'Bank Debt/Senior Secured Investments',
        'Subordinated Debt/Corporate Notes',
        'Total Common Equity/Partnership Interests / Warrants',
        'Cash Equivalents',
        'Secured Debt')
    ))

def standard_field_names()->tuple:
    return (
        'Description',
        'interest',
        'Fair Value',
        'portfolio',
        'footnotes',
        'Industry',
        'floor',
        'Maturity',
        'Amount',
        'investment',
        'date',
        'Shares',
        'Spread Above Index',
        'interest',
        'Acquisition Date',
        'name of issuer',
        'gross additions',
        'gross reductions',
        'realized gain loss',
        'change in unrealized gain loss',
        'cash equivalents',
    )

def company_control_headers()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        (
        'control investments',
        'affiliate investments',
        'non-control/non-affilate investments',
        'Non-Controlled/Non-Affiliated  Investments:',
        'Affiliated  Investments:',
        'Non-Controlled/Non-Affiliated  Investments  :',
        'Affiliated  Investments  :',
        'Non-controlled/Non-affiliated Investments',
        'Affiliated Investments',
        )
    ))

def strip_string(
    columns_names:list,
    standardize:bool=False
)->tuple:
    columns = tuple(map(lambda col:re.sub(r'[^a-z]', '', str(col).lower()),columns_names))
    if standardize:
        standard_fields = standard_field_names()
        return tuple(
            get_standard_name(col,standard_fields) for col in columns
        )
    return columns

def get_key_fields(
    df_cur:pd.DataFrame
)->tuple:
    important_fields = standard_field_names() + common_subheaders()
    for idx,row in enumerate(df_cur.iterrows()):
        found = any(any(
            key in str(field).lower() 
            for key in important_fields)
                    for field in row[-1].dropna().tolist()
            )
        if found and len(set(row[-1].dropna().tolist())) >= 5:
            fields = strip_string(row[-1].tolist(),standardize=found) ,idx
            return fields
    return strip_string(df_cur.iloc[0].tolist(),standardize=found),0

# Function to extract date and convert to datetime object
def extract_date(file_path):
    # Extract date from file path (assuming date is always in 'YYYY-MM-DD' format)
    date_str = re.search(r'\d{4}-\d{2}-\d{2}', file_path).group()
    return datetime.datetime.strptime(date_str, '%Y-%m-%d')

def remove_row_duplicates(row):
    seen = set()
    return pd.Series([x if x not in seen and not seen.add(x) else None for x in row])


def merge_duplicate_columns(
    df:pd.DataFrame,
)->pd.DataFrame:
    duplicate_cols = df.columns[df.columns.duplicated(keep=False)]
    for col_name in duplicate_cols.unique():
        duplicate_data = df.loc[:, df.columns == col_name]
        merged_data = duplicate_data.apply(lambda row: ' '.join(set(row.dropna().astype(str))), axis=1)
        df = df.loc[:, df.columns != col_name]
        df[col_name] = merged_data
    return df

def extract_subheaders(
    df:pd.DataFrame,
    control:bool,
)->pd.DataFrame:
    col_name = 'company_control' if control else 'TypeofInvestment'
    if col_name in df.columns:
        return df
    include = df.apply(
        lambda row: re.search('|'.join(company_control_headers() if control else common_subheaders()), str(row[0]), re.IGNORECASE) is not None,
        axis=1
    )  
    
    exclude = ~df.apply(
        lambda row: row.astype(str).str.contains('total|Inc|Ltd|LLC|Holdings|LP|Co|Corporation', case=False, na=False).any(),
        axis=1
    )
    idx = df[include & exclude].index.tolist()
    df[col_name] = None
    if not idx:
        return df

    prev_header = subheader = None
    df.loc[idx[-1]:,col_name] = df.iloc[idx[-1],1] if isinstance(df.iloc[idx[-1],0],float)  else df.iloc[idx[-1],0]
    for j,i in enumerate(idx[:-1]):
        prev_header = subheader
        subheader = df.iloc[i,1] if isinstance(df.iloc[i,0],float)  else df.iloc[i,0]
        df.loc[idx[j]:idx[j+1],col_name] = subheader if subheader != '' else prev_header
    # df.drop(idx,axis=0,inplace=True,errors='ignore') 
    return df



def _clean(
    file_path:str,
    regex_pattern:str=r'\w+\s+\d{1,2},\s+\d{4}'
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0)
    df.dropna(axis=0,how='all',inplace=True)
    df = df[~df.apply(lambda row:row.str.match(regex_pattern).all(),axis=1)]

    important_fields,idx = get_key_fields(df)
    df.columns = important_fields
    col_drop_filter = 1 if df.shape[0] < 10 else 4    

    df = merge_duplicate_columns(df).reset_index(drop=True)
    df.replace(['\u200b','%',' ','','%(7)','7)','(6)','(8)','(5)','%(5)','% $','K','(7)','$ %','% C$',')',')†','% (11)',')† )'],np.nan,inplace=True) #':','$','%'
    
    duplicate_idx = df.apply(lambda row:row.duplicated().sum() > 3,axis=1)  
    df.loc[duplicate_idx].apply(remove_row_duplicates, axis=1)  
    # df.loc[duplicate_idx] = df.loc[duplicate_idx].apply(remove_row_duplicates, axis=1)
    df = df.applymap(lambda e:np.nan if e is None else e)
    columns = (~df.isna()).sum(axis=0) <= col_drop_filter
    to_drop = columns[columns].index.tolist()+['nan'] if 'nan' in df.columns else columns[columns].index.tolist()
    df.drop(columns=to_drop,inplace=True)

    return df.reset_index(drop=True)

cik = 1418076
ROOT_PATH = r'C:\Users\pysol\Desktop\projects\sec_filings'

def main()->None:
    bdc = os.path.join(ROOT_PATH,str(cik))
    qtrs = os.listdir(bdc)
    stop = stopping_criterion()
    for qtr in qtrs:
        if '.csv' in qtr or not os.path.exists(os.path.join(bdc,qtr,f'Schedule_of_Investments_0.csv')):
            continue
        # qtr = '2017-12-31'
        print(qtr)

        index_list_sum = i = 0
        soi_files = sorted([
            os.path.join(bdc,qtr,file) 
            for file in os.listdir(os.path.join(bdc,qtr))
            if '.csv' in file
        ],key=lambda f: int(f.split('_')[-1].split('.')[0]))
        df = _clean(soi_files[i])
        index_list = df.apply(
            lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
            axis=1
        )
        index_list_sum = index_list.sum()
        dfs = [df]     
        i += 1
        cols = df.columns.tolist()
        while index_list_sum == 0 :
            print(soi_files[i])
            df = _clean(soi_files[i])

            dfs.append(df)
            index_list = df.apply(
                lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
                axis=1
            )
            index_list_sum = index_list.sum()
            i += 1
            
        date_final = dfs[0]
        if len(dfs) > 1:
            date_final = pd.concat(dfs,axis=0,ignore_index=True)#pd.DataFrame(concat(*dfs))
        # date_final = extract_subheaders(date_final,control=True)
        # date_final = extract_subheaders(date_final,control=False)

        date_final['qtr'] = qtr.split('\\')[-1]
        if not os.path.exists(os.path.join(bdc,qtr,'output')):
            os.makedirs(os.path.join(bdc,qtr,'output'))
        columns_to_drop = date_final.notna().sum() <= 2
        date_final.drop(columns=columns_to_drop[columns_to_drop].index)
        date_final.to_csv(os.path.join(bdc,qtr,'output',f'{qtr}.csv'),index=False)
        # break
        
    # Use glob to find files
    files = sorted(glob.glob(f'{cik}/*/output/*.csv'), key=extract_date)
    single_truth = pd.concat([
        pd.read_csv(df) for df in files
    ],axis=0,ignore_index=True)
    single_truth.drop(columns=single_truth.columns[['Unnamed' in col for col in single_truth.columns]],inplace=True)
    single_truth.to_csv(os.path.join(str(cik),f'{cik}_soi_table.csv'),index=False)
    
import warnings

# Suppress future warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.filterwarnings('ignore', category=pd.errors.SettingWithCopyWarning)
main()

2009-12-31
C:\Users\pysol\Desktop\projects\sec_filings\1418076\2009-12-31\Schedule_of_Investments_1.csv
2010-03-31
C:\Users\pysol\Desktop\projects\sec_filings\1418076\2010-03-31\Schedule_of_Investments_1.csv
2010-06-30
C:\Users\pysol\Desktop\projects\sec_filings\1418076\2010-06-30\Schedule_of_Investments_1.csv
2010-09-30
C:\Users\pysol\Desktop\projects\sec_filings\1418076\2010-09-30\Schedule_of_Investments_1.csv
2010-12-31
C:\Users\pysol\Desktop\projects\sec_filings\1418076\2010-12-31\Schedule_of_Investments_1.csv
2011-03-31
C:\Users\pysol\Desktop\projects\sec_filings\1418076\2011-03-31\Schedule_of_Investments_1.csv
2011-06-30
C:\Users\pysol\Desktop\projects\sec_filings\1418076\2011-06-30\Schedule_of_Investments_1.csv
2011-09-30
C:\Users\pysol\Desktop\projects\sec_filings\1418076\2011-09-30\Schedule_of_Investments_1.csv
2011-12-31
C:\Users\pysol\Desktop\projects\sec_filings\1418076\2011-12-31\Schedule_of_Investments_1.csv
2012-03-31
C:\Users\pysol\Desktop\projects\sec_filings\1418076\2

In [16]:
def remove_row_duplicates(row:str)->pd.Series:
    seen = set()
    return pd.Series([x if x not in seen and not seen.add(x) else None for x in row])

def _clean(
    file_path:str,
    regex_pattern:str=r'\w+\s+\d{1,2},\s+\d{4}'
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0)
    df.dropna(axis=0,how='all',inplace=True)
    df = df[~df.apply(lambda row:row.str.match(regex_pattern).all(),axis=1)]

    important_fields,idx = get_key_fields(df)
    df.columns = important_fields
    col_drop_filter = 1 if df.shape[0] < 10 else 4    

    df = merge_duplicate_columns(df).reset_index(drop=True)
    df.replace(['\u200b','%',' ','','%(7)','7)','(6)','(8)','(5)','%(5)','% $','K','(7)','$ %','% C$',')',')†','% (11)',')† )'],np.nan,inplace=True) #':','$','%'
    
    duplicate_idx = df.apply(lambda row:row.duplicated().sum() > 3,axis=1)  
    df.loc[duplicate_idx].apply(remove_row_duplicates, axis=1)  
    # df.loc[duplicate_idx] = df.loc[duplicate_idx].apply(remove_row_duplicates, axis=1)
    df = df.applymap(lambda e:np.nan if e is None else e)
    columns = (~df.isna()).sum(axis=0) <= col_drop_filter
    to_drop = columns[columns].index.tolist()+['nan'] if 'nan' in df.columns else columns[columns].index.tolist()
    df.drop(columns=to_drop,inplace=True)

    return df.reset_index(drop=True)


file_path = r'C:\Users\pysol\Desktop\projects\sec_filings\1418076\2011-06-30\Schedule_of_Investments_1.csv'
stop = stopping_criterion()
df = _clean(file_path)
index_list = df.apply(
    lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
    axis=1
)
index_list_sum = index_list.sum()
index_list_sum


1

In [17]:
df

Description  \
0                                    Description  (1)   
1                            Preferred Equity — 0.92%   
2                             SODO Corp. (10)(13)(21)   
3                            SOCAY Corp. (10)(13)(22)   
4                                   Wyle Laboratories   
5                              Total Preferred Equity   
6   Common Equity / Partnership Interests / Warran...   
7             Ark Real Estate Partners LP (9)(11)(12)   
8                                     Direct Buy Inc.   
9                    Global Garden Products (3)(4)(6)   
10                                        Grakon, LLC   
11                               Grakon, LLC Warrants   
12                     Great American Group Inc. (14)   
13                     Great American Group Inc. (15)   
14                 National Specialty Alloys, LLC(10)   
15                           Nuveen Investments, Inc.   
16        NXP Semiconductors Netherlands B.V.(3) (17)   
17                           Seven West Media Limited   
18  Total Common Equity/Partnerships Interests / W...   
19                                                NaN   
20                                  Total Investments   

                                         Industry               Amount  \
0                                        Industry  Par Amount/  Shares   
1                                             NaN                  NaN   
2                             Aerospace & Defense                  899   
3                             Aerospace & Defense                 8081   
4                             Aerospace & Defense                  387   
5                                             NaN                  NaN   
6                                             NaN                  NaN   
7                                     Real Estate             38085500   
8   Home and Office Furnishing, Consumer Products              5000000   
9                           Farming & Agriculture                88483   
10                                      Machinery              1714286   
11                                      Machinery              3518001   
12              Personal, Food and Misc. Services               572800   
13              Personal, Food and Misc. Services               187500   
14    Mining, Steel, Iron, and Nonprecious Metals              1000000   
15                                        Finance              3486444   
16                                    Electronics               645292   
17                   Broadcasting & Entertainment               437687   
18                                            NaN                  NaN   
19                                            NaN                  NaN   
20                                            NaN                  NaN   

         cost   Fair Value  
0        Cost  Fair  Value  
1         NaN          NaN  
2       $ 922        $ 922  
3        8286         8286  
4          39           45  
5      $ 9247       $ 9253  
6         NaN          NaN  
7     $ 38086      $ 31825  
8        5000          250  
9           —            —  
10       1714            —  
11          —            —  
12       2681          172  
13          3           56  
14      10000        13000  
15      30875        19524  
16      17592        16947  
17       2424         1901  
18        NaN          NaN  
19   $ 108375      $ 83675  
20  $ 1067033    1004495 $

# cik==1544206

In [10]:
import os
import re
import glob
import datetime
import pandas as pd
import numpy as np
from fuzzywuzzy import process

def get_standard_name(col, choices, score_cutoff=60):
    best_match, score = process.extractOne(col, choices)
    if score > score_cutoff:
        return best_match
    return col

def stopping_criterion(
    qtr:str,
    # search_string:str='total investments',
)->str:
    # Regular expression to ignore whitespace and case
    # Define the dates as datetime objects
    qtr = datetime.datetime.strptime(qtr, '%Y-%m-%d')
    check = datetime.datetime.strptime('2016-03-31', '%Y-%m-%d')
    if qtr >= check:
        # regex_pattern = search_string.replace(' ', r'\s*')
        return '{}|{}'.format(r'^\s*(Total)\s*$',r'\bTotal Investments\b(?!\s*—[^—]+)')
    return '{}'.format(r'\s*Total\s*Investments\s*—non-controlled/non-affiliated')

def concat(*dfs)->list:
    final = []
    for df in dfs:
        final.extend(df.values.tolist())
    return final

def common_subheaders()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        ('senior secured loans',
        'first lien',
        'second lien',
        'senior secured bonds',
        'subordinated debt',
        'equity/other',
        'collateralized securities',
        'preferred equity—',
        'Equity/Warrants',
        'unsecured debt',
        'senior secured notes',
        'warrants',
        'total senior secured first lien term loans',
        'Secured Debt')
    ))
    
def standard_field_names()->tuple:
    return (
        'portfolio',
        'footnotes',
        'industry',
        'reference rate',
        'interest rate', 
        'Par  Amount/  LLC  Interest',# TODO check interest rate or jsut interest
        'floor',
        'maturity',
        'principal amount', # TODO change stand names for more dynamic fuzzywuzzy matching
        'cost',
        'value',
        'investment',
        'date',
        'subheaders',
        'number of shares',
        'of net assets',
        'type',
        'effective yield',
        'share units'
    )

def company_control_headers()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        (
        'control investments',
        'affiliate investments',
        'non-control/non-affilate investments',
        'Non-Controlled/Non-Affiliated  Investments:',
        'Affiliated  Investments:',
        'Non-Controlled/Non-Affiliated  Investments  :',
        'Affiliated  Investments  :',
        'Non-controlled/Non-affiliated Investments',
        'Affiliated Investments',
        )
    ))

def strip_string(
    columns_names:list,
    standardize:bool=False
)->tuple:
    columns = tuple(map(lambda col:re.sub(r'[^a-z]', '', str(col).lower()),columns_names))
    if standardize:
        standard_fields = standard_field_names()
        return tuple(
            get_standard_name(col,standard_fields) for col in columns
        )
    return columns

def get_key_fields(
    df_cur:pd.DataFrame
)->tuple:
    important_fields = standard_field_names() + common_subheaders()
    for idx,row in enumerate(df_cur.iterrows()):
        found = any(any(
            key in str(field).lower() 
            for key in important_fields)
                    for field in row[-1].dropna().tolist()
            )
        if found and len(set(row[-1].dropna().tolist())) >= 5:
            fields = strip_string(row[-1].tolist(),standardize=found) ,idx
            return fields
    return strip_string(df_cur.iloc[0].tolist(),standardize=found),0

# Function to extract date and convert to datetime object
def extract_date(file_path):
    # Extract date from file path (assuming date is always in 'YYYY-MM-DD' format)
    date_str = re.search(r'\d{4}-\d{2}-\d{2}', file_path).group()
    return datetime.datetime.strptime(date_str, '%Y-%m-%d')



def merge_duplicate_columns(
    df:pd.DataFrame,
)->pd.DataFrame:
    duplicate_cols = df.columns[df.columns.duplicated(keep=False)]
    for col_name in duplicate_cols.unique():
        duplicate_data = df.loc[:, df.columns == col_name]
        merged_data = duplicate_data.apply(lambda row: ' '.join(set(row.dropna().astype(str))), axis=1)
        df = df.loc[:, df.columns != col_name]
        df[col_name] = merged_data
    return df

def extract_subheaders(
    df:pd.DataFrame,
    control:bool,
)->pd.DataFrame:
    col_name = 'company control' if control else 'Type of Investment'
    if col_name in df.columns:
        return df
    include = df.apply(
        lambda row: re.search('|'.join(company_control_headers() if control else common_subheaders()), str(row[0]), re.IGNORECASE) is not None,
        axis=1
    )  
    
    exclude = ~df.apply(
        lambda row: row.astype(str).str.contains('total|Inc|Ltd|LLC|Holdings|LP|Co|Corporation', case=False, na=False).any(),
        axis=1
    )
    idx = df[include & exclude].index.tolist()
    df[col_name] = None
    if not idx:
        return df

    prev_header = subheader = None
    df.loc[idx[-1]:,col_name] = df.iloc[idx[-1],1] if isinstance(df.iloc[idx[-1],0],float)  else df.iloc[idx[-1],0]
    for j,i in enumerate(idx[:-1]):
        prev_header = subheader
        subheader = df.iloc[i,1] if isinstance(df.iloc[i,0],float)  else df.iloc[i,0]
        df.loc[idx[j]:idx[j+1],col_name] = subheader if subheader != '' else prev_header
    return df

def remove_row_duplicates(row:pd.Series)->pd.Series: 
    out = []
    for v in row:
        if v in out:
            out.append(np.nan)
        else:
            out.append(v)
    return pd.Series(out)


def _clean(
    file_path:str,
    regex_pattern:str=r'\w+\s+\d{1,2},\s+\d{4}',
    exceptions:list=['2022-09-30\Schedule_of_Investments_6.csv','2013-06-30\Schedule_of_Investments_1.csv']
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0)
    df.dropna(axis=0,how='all',inplace=True)
    df = df[~df.apply(lambda row:row.str.match(regex_pattern).all(),axis=1)]

    important_fields,idx = get_key_fields(df)
    df.columns = important_fields
    
    df = merge_duplicate_columns(df).reset_index(drop=True)
    df.replace(['\u200b','%',' ','','^'],np.nan,inplace=True) #':','$','%'
    if pd.Series([e in file_path for e in exceptions]).sum():
        return df
    to_drop = 1 if df.shape[0] < 10 else 3 
    columns = (~df.isna()).sum(axis=0) <= to_drop
    df.drop(columns=columns[columns].index,inplace=True)
    duplicate_idx = df.apply(lambda row:row[pd.to_numeric(row,errors='coerce').isna()].duplicated().sum() > 1 ,axis=1)
    clean_rows = df.loc[duplicate_idx].apply(remove_row_duplicates, axis=1).reset_index(drop=True)
    j = 0
    for i,flag in enumerate(duplicate_idx):
        if not flag:
            continue
        df.iloc[i,:] = clean_rows.loc[j,:]
        j += 1
    return df.reset_index(drop=True)


cik = 1544206
ROOT_PATH = r'C:\Users\pysol\Desktop\projects\sec_filings'

def main()->None:
    bdc = os.path.join(ROOT_PATH,str(cik))
    qtrs = os.listdir(bdc)
    for qtr in qtrs:
        if '.csv' in qtr or not os.path.exists(os.path.join(bdc,qtr,f'Schedule_of_Investments_0.csv')):
            continue
        # qtr = '2024-03-31'
        print(qtr)
        stop = stopping_criterion(qtr)
        index_list_sum = i = 0
        df = _clean(os.path.join(bdc,qtr,f'Schedule_of_Investments_{i}.csv'))
        index_list = df.apply(
            lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
            axis=1
        )
        index_list_sum = index_list.sum()
        dfs = [df]     
        i += 1
        cols = df.columns.tolist()
        while index_list_sum == 0 :
            print(os.path.join(bdc,qtr,f'Schedule_of_Investments_{i}.csv'))
            df = _clean(os.path.join(bdc,qtr,f'Schedule_of_Investments_{i}.csv'))
            if set(list(range(10))) >= set(df.columns.tolist()):
                df.columns = cols
            dfs.append(df)
            index_list = df.apply(
                lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
                axis=1
            )
            index_list_sum = index_list.sum()
            i += 1
            
        date_final = dfs[0]
        if len(dfs) > 1:
            date_final = pd.concat(dfs,axis=0,ignore_index=True)#pd.DataFrame(concat(*dfs))
        date_final = extract_subheaders(date_final,control=True)
        date_final = extract_subheaders(date_final,control=False)

        date_final['qtr'] = qtr.split('\\')[-1]
        if not os.path.exists(os.path.join(bdc,qtr,'output')):
            os.makedirs(os.path.join(bdc,qtr,'output'))
        columns_to_drop = date_final.notna().sum() <= 2
        date_final.drop(columns=columns_to_drop[columns_to_drop].index)
        date_final.to_csv(os.path.join(bdc,qtr,'output',f'{qtr}.csv'),index=False)
        # break
    # Use glob to find files
    files = sorted(glob.glob(f'{cik}/*/output/*.csv'), key=extract_date)
    single_truth = pd.concat([
        pd.read_csv(df) for df in files
    ],axis=0,ignore_index=True)
    single_truth['portfolio'] = single_truth['portfolio'].combine_first(single_truth['investment'])
    single_truth.drop(columns=['investment','nan'], axis=1, inplace=True)
    single_truth.to_csv(os.path.join(str(cik),f'{cik}_soi_table.csv'),index=False)
    
    
import warnings

# Suppress future warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.filterwarnings('ignore', category=pd.errors.SettingWithCopyWarning)
main()
# FIX 2015 onward small panels missing data
# Interest rate & Reference rate 2019 onwards
# catch the total debt investment dulicate 2019-03-31

2013-06-30
2013-09-30
2013-12-31
C:\Users\pysol\Desktop\projects\sec_filings\1544206\2013-12-31\Schedule_of_Investments_1.csv
2014-03-31
C:\Users\pysol\Desktop\projects\sec_filings\1544206\2014-03-31\Schedule_of_Investments_1.csv
C:\Users\pysol\Desktop\projects\sec_filings\1544206\2014-03-31\Schedule_of_Investments_2.csv
2014-06-30
C:\Users\pysol\Desktop\projects\sec_filings\1544206\2014-06-30\Schedule_of_Investments_1.csv
C:\Users\pysol\Desktop\projects\sec_filings\1544206\2014-06-30\Schedule_of_Investments_2.csv
C:\Users\pysol\Desktop\projects\sec_filings\1544206\2014-06-30\Schedule_of_Investments_3.csv
2014-09-30
C:\Users\pysol\Desktop\projects\sec_filings\1544206\2014-09-30\Schedule_of_Investments_1.csv
C:\Users\pysol\Desktop\projects\sec_filings\1544206\2014-09-30\Schedule_of_Investments_2.csv
2014-12-31
C:\Users\pysol\Desktop\projects\sec_filings\1544206\2014-12-31\Schedule_of_Investments_1.csv
C:\Users\pysol\Desktop\projects\sec_filings\1544206\2014-12-31\Schedule_of_Investments

C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:220: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:220: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:220: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:220: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actuall

C:\Users\pysol\Desktop\projects\sec_filings\1544206\2016-03-31\Schedule_of_Investments_2.csv
C:\Users\pysol\Desktop\projects\sec_filings\1544206\2016-03-31\Schedule_of_Investments_3.csv


C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actuall

C:\Users\pysol\Desktop\projects\sec_filings\1544206\2016-03-31\Schedule_of_Investments_4.csv
C:\Users\pysol\Desktop\projects\sec_filings\1544206\2016-03-31\Schedule_of_Investments_5.csv


...

C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actuall

C:\Users\pysol\Desktop\projects\sec_filings\1544206\2024-03-31\Schedule_of_Investments_5.csv
C:\Users\pysol\Desktop\projects\sec_filings\1544206\2024-03-31\Schedule_of_Investments_6.csv


C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actuall

C:\Users\pysol\Desktop\projects\sec_filings\1544206\2024-03-31\Schedule_of_Investments_7.csv
C:\Users\pysol\Desktop\projects\sec_filings\1544206\2024-03-31\Schedule_of_Investments_8.csv


C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\1036385718.py:234: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actuall

In [7]:
def remove_row_duplicates(row:pd.Series)->pd.Series: 
    out = []
    for v in row:
        if v in out:
            out.append(np.nan)
        else:
            out.append(v)
    return pd.Series(out)

def standard_field_names()->tuple:
    return (
        'portfolio',
        'footnotes',
        'industry',
        'reference rate',
        'interest rate', 
        'Par  Amount/  LLC  Interest',# TODO check interest rate or jsut interest
        'floor',
        'maturity',
        'principal amount', # TODO change stand names for more dynamic fuzzywuzzy matching
        'cost',
        'value',
        'investment',
        'date',
        'subheaders',
        'number of shares',
        'of net assets',
        'type',
        'effective yield',
        'share units'
    )

def _clean(
    file_path:str,
    regex_pattern:str=r'\w+\s+\d{1,2},\s+\d{4}',
    exceptions:list=['2022-09-30\Schedule_of_Investments_6.csv','2013-06-30\Schedule_of_Investments_1.csv']
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0)
    df.dropna(axis=0,how='all',inplace=True)
    df = df[~df.apply(lambda row:row.str.match(regex_pattern).all(),axis=1)]

    important_fields,idx = get_key_fields(df)
    df.columns = important_fields
    
    df = merge_duplicate_columns(df).reset_index(drop=True)
    df.replace(['\u200b','%',' ','','^'],np.nan,inplace=True) #':','$','%'
    if pd.Series([e in file_path for e in exceptions]).sum():
        return df
    to_drop = 1 if df.shape[0] < 10 else 3 
    columns = (~df.isna()).sum(axis=0) <= to_drop
    df.drop(columns=columns[columns].index,inplace=True)
    duplicate_idx = df.apply(lambda row:row[pd.to_numeric(row,errors='coerce').isna()].duplicated().sum() > 1 ,axis=1)
    clean_rows = df.loc[duplicate_idx].apply(remove_row_duplicates, axis=1).reset_index(drop=True)
    j = 0
    for i,flag in enumerate(duplicate_idx):
        if not flag:
            continue
        df.iloc[i,:] = clean_rows.loc[j,:]
        j += 1
    return df.reset_index(drop=True)



stop = '{}|{}'.format(r'^\s*(Total)\s*$',r'\bTotal Investments\b(?!\s*—[^—]+)')
file_path = r'C:\Users\pysol\Desktop\projects\sec_filings\1544206\2016-06-30\Schedule_of_Investments_5.csv'

df = _clean(file_path)
index_list = df.apply(
    lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
    axis=1
)
index_list_sum = index_list.sum()
index_list_sum
# check pandas row value can be cast to float or not



C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\3304728907.py:69: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\3304728907.py:69: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\3304728907.py:69: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
C:\Users\pysol\AppData\Local\Temp\ipykernel_1580\3304728907.py:69: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually ge

1

In [8]:
df

investment         industry  \
0                  Investments—controlled/affiliated         Industry   
1                       Investment Fund (1.22%)  (8)              NaN   
2  Middle Market Credit Fund, LLC, Mezzanine Loan...  Investment Fund   
3  Middle Market Credit Fund, LLC, Subordinated L...  Investment Fund   
4                              Investment Fund Total              NaN   
5                                  Total investments              NaN   

    interest rate        maturity  Par  Amount/  LLC  Interest       cost  \
0  Interest  Rate  Maturity  Date  Par  Amount/  LLC  Interest       Cost   
1             NaN             NaN                          NaN        NaN   
2           10.15       6/24/2017                       1000 $        NaN   
3           0.001        3/1/2021                        14001      14001   
4             NaN             NaN                          NaN    $ 15001   
5             NaN             NaN                          NaN  $ 1220872   

              value              of net assets  
0  Fair  Value  (7)  Percentage of  Net Assets  
1               NaN                        NaN  
2               NaN                       0.15  
3             13714                       2.09  
4           14714 $                       2.24  
5         1201234 $                     182.58

# cik==1370755

In [1]:
import os
import re
import glob
import logging
import datetime
import pandas as pd
import numpy as np
from fuzzywuzzy import process

'''
TO DO 
separate issuer investment
make issuer would have company name

June 30 2021

start Black rock capital investment core BKCC (cik==1326003)
'''
# https://www.sec.gov/robots.txt
def get_standard_name(col, choices, score_cutoff=60):
    best_match, score = process.extractOne(col, choices)
    if score > score_cutoff:
        return best_match
    return col

def stopping_criterion()->str:
    return '{}'.format(r'Total\s*Investments')

def exceptions(bdc:str)->list:
    return [
        os.path.join(bdc,'2015-03-31\Schedule_of_Investments_4.csv'),
        os.path.join(bdc,'2015-03-31\Schedule_of_Investments_1.csv'),
        os.path.join(bdc,'2015-03-31\Schedule_of_Investments_7.csv'),
        os.path.join(bdc,'2015-03-31\Schedule_of_Investments_10.csv'),
        os.path.join(bdc,'2015-06-30\Schedule_of_Investments_1.csv'),
        os.path.join(bdc,'2015-06-30\Schedule_of_Investments_4.csv'),
        os.path.join(bdc,'2015-06-30\Schedule_of_Investments_7.csv'),
        os.path.join(bdc,'2015-06-30\Schedule_of_Investments_10.csv'),
    ]

def concat(*dfs)->list:
    final = []
    for df in dfs:
        final.extend(df.values.tolist())
    return final

def common_subheaders()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        ('Advertising, Public Relations and Marketing ',
        'Air Transportation',
        'Amusement and Recreation',
        'Apparel Manufacturing',
        'Building Equipment Contractors',
        'Business Support Services',
        'Chemicals',
        'Communications Equipment Manufacturing',
        'Credit Related Activities',
        'Computer Systems Design and Related Services',
        'Credit (Nondepository)',
        'Data Processing and Hosting Services',
        'Educational Support Services',
        'Electronic Component Manufacturing',
        'Equipment Leasing',
        'Facilities Support Services',
        'Grocery Stores',
        'Hospitals',
        'Insurance',
        'Lessors of Nonfinancial Licenses',
        'Management, Scientific, and Technical Consulting Services',
        'Motion Picture and Video Industries',
        'Other Information Services',
        'Other Manufacturing',
        'Other Publishing',
        'Other Real Estate Activities',
        'Other Telecommunications',
        'Plastics Manufacturing',
        'Radio and Television Broadcasting',
        'Real Estate Leasing',
        'Restaurants',
        'Retail',
        'Satellite Telecommunications',
        'Scientific Research and Development Services',
        'Texttile Furnishings Mills',
        'Traveler Arrangement',
        'Software Publishing',
        'Utility System Construction',
        'Wholesalers',
        'Wired Telecommunications Carriers',
        'Wireless Telecommunications Carriers',
        )
    ))

def standard_field_names()->tuple:
    return (
        'portfolio',
        'footnotes',
        'industry',
        'rate',
        'floor',
        'maturity',
        'principal amount', # TODO change stand names for more dynamic fuzzywuzzy matching
        'cost',
        'fair value',
        'investment',
        'date',
        'subheaders',
        'number of shares',
        'of net assets',
        'type',
        'effective yield',
        'share units',
        'Percent of Case and Investments',
        '\\% of Portfolio'
    )

def company_control_headers()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        (
        'Debt Investments',
        'Debt Investments (82.23%)',
        'Debt Investments (A)',
        'Debt Investments (continued)',
        'Equity Securities',
        'Equity Securities (continued)',
        'Cash and Cash Equivalents',
        )
    ))

def strip_string(
    columns_names:list,
    standardize:bool=False
)->tuple:
    # columns = tuple(map(lambda col:re.sub(r'[^a-z]', '', str(col).lower()),columns_names))
    if standardize:
        standard_fields = standard_field_names()
        return tuple(
            re.sub(r'\s+', '_',get_standard_name(col,standard_fields)) for col in columns_names
        )
    return tuple(re.sub(r'\s+', '_',col) for col in columns_names)

def get_key_fields(
    df_cur:pd.DataFrame
)->tuple:
    important_fields = standard_field_names() + common_subheaders()
    for idx,row in enumerate(df_cur.iterrows()):
        found = any(any(
            key in str(field).lower() 
            for key in important_fields)
                    for field in row[-1].dropna().tolist()
            )
        if found and len(set(row[-1].dropna().tolist())) >= 4:
            cols = df_cur.iloc[:idx + 1].apply(lambda row: ' '.join(row.dropna()), axis=0).tolist()
            fields = strip_string(cols,standardize=found) ,idx
            return fields
    return strip_string(df_cur.iloc[0].tolist(),standardize=found),0


# Function to extract date and convert to datetime object
def extract_date(file_path):
    # Extract date from file path (assuming date is always in 'YYYY-MM-DD' format)
    date_str = re.search(r'\d{4}-\d{2}-\d{2}', file_path).group()
    return datetime.datetime.strptime(date_str, '%Y-%m-%d')

def remove_row_duplicates(row):
    seen = set()
    return pd.Series([x if x not in seen and not seen.add(x) else None for x in row])


def merge_duplicate_columns(
    df:pd.DataFrame,
)->pd.DataFrame:
    duplicate_cols = df.columns[df.columns.duplicated(keep=False)]
    for col_name in duplicate_cols.unique():
        duplicate_data = df.loc[:, df.columns == col_name]
        merged_data = duplicate_data.apply(lambda row: ' '.join(set(row.dropna().astype(str))), axis=1)
        df = df.loc[:, df.columns != col_name]
        df[col_name] = merged_data
    return df

def extract_subheaders(
    df:pd.DataFrame,
    control:bool,
)->pd.DataFrame:
    col_name = 'company_control' if control else 'Type_of_Investment'
    if col_name in df.columns:
        return df
    include = df.apply(
        lambda row: re.search('|'.join(company_control_headers() if control else common_subheaders()), str(row[0]), re.IGNORECASE) is not None,
        axis=1
    )  
    
    exclude = ~df.apply(
        lambda row: row.astype(str).str.contains('total|Inc|Ltd|LLC|Holdings|LP|Co|Corporation', case=False, na=False).any(),
        axis=1
    )
    idx = df[include & exclude].index.tolist()
    df[col_name] = None
    if not idx:
        return df

    prev_header = subheader = None
    df.loc[idx[-1]:,col_name] = df.iloc[idx[-1],1] if isinstance(df.iloc[idx[-1],0],float)  else df.iloc[idx[-1],0]
    for j,i in enumerate(idx[:-1]):
        prev_header = subheader
        subheader = df.iloc[i,1] if isinstance(df.iloc[i,0],float)  else df.iloc[i,0]
        df.loc[idx[j]:idx[j+1],col_name] = subheader if subheader != '' else prev_header
    return df

def _clean(
    file_path:str,
    regex_pattern:str=r'\w+\s+\d{1,2},\s+\d{4}',
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0,na_values=[' ', ''])
        
    df.replace(['\u200b',None, r'^\s*$'],np.nan,regex=True,inplace=True) #':','$','%'
    df.dropna(axis=0,how='all',inplace=True)
    
    df = df[~df.apply(lambda row:row.astype(str).str.match(regex_pattern).all(),axis=1)]
    important_fields,idx = get_key_fields(df)
    df.columns = important_fields
    df = merge_duplicate_columns(df).reset_index(drop=True)
    
    duplicate_idx = df.apply(lambda row:(row != np.nan).duplicated().sum() > 7 ,axis=1)
    df.loc[duplicate_idx] = df.loc[duplicate_idx].apply(remove_row_duplicates, axis=1)
    
    df.replace([r'^\s*$'],np.nan,regex=True,inplace=True) #':','$','%'
    df.dropna(axis=1,how='all',inplace=True)
    
    columns = (~df.isna()).sum(axis=0) <= 3
    df.drop(columns=df.columns[columns],inplace=True)
    return df.reset_index(drop=True)



cik = 1370755
ROOT_PATH = r'C:\Users\pysol\Desktop\projects\sec_filings'

def main()->None:
    bdc = os.path.join(ROOT_PATH,str(cik))
    qtrs = os.listdir(bdc)
    stop = stopping_criterion()
    for qtr in qtrs:
        if '.csv' in qtr or not os.path.exists(os.path.join(bdc,qtr,f'Schedule_of_Investments_0.csv')):
            continue
        # qtr = '2014-06-30'
        print(qtr)
        index_list_sum = i = 0
        soi_files = sorted([
            os.path.join(bdc,qtr,file) 
            for file in os.listdir(os.path.join(bdc,qtr))
            if '.csv' in file
        ],key=lambda f: int(f.split('_')[-1].split('.')[0]))
        df = _clean(soi_files[i])
        index_list = df.apply(
            lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
            axis=1
        )
        index_list_sum = index_list.sum()
        dfs = [df]     
        i += 1
        cols = df.columns.tolist()
        while index_list_sum == 0 :
            if soi_files[i] in exceptions(bdc):
                i += 1
                continue
            print(soi_files[i])
            df = _clean(soi_files[i])
            if set(list(range(10))) >= set(df.columns.tolist()):
                df.columns = cols
            dfs.append(df)
            index_list = df.apply(
                lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
                axis=1
            )
            index_list_sum = index_list.sum()
            i += 1
            
        date_final = dfs[0]
        if len(dfs) > 1:
            date_final = pd.concat(dfs,axis=0,ignore_index=True)#pd.DataFrame(concat(*dfs))
        date_final = extract_subheaders(date_final,control=True)
        date_final = extract_subheaders(date_final,control=False)

        date_final['qtr'] = qtr.split('\\')[-1]
        if not os.path.exists(os.path.join(bdc,qtr,'output')):
            os.makedirs(os.path.join(bdc,qtr,'output'))
        columns_to_drop = date_final.notna().sum() <= 2
        date_final.drop(columns=columns_to_drop[columns_to_drop].index)
        date_final.to_csv(os.path.join(bdc,qtr,'output',f'{qtr}.csv'),index=False)
        # break
    # Use glob to find files
    files = sorted(glob.glob(f'{cik}/*/output/*.csv'), key=extract_date)
    single_truth = pd.concat([
        pd.read_csv(df) for df in files
    ],axis=0,ignore_index=True)
    # single_truth['investment'] = single_truth['investment'].combine_first(single_truth['Issuer'])
    # single_truth.drop(columns=['Issuer'], axis=1, inplace=True)
    single_truth.drop(columns=single_truth.columns[['Unnamed' in col for col in single_truth.columns]],inplace=True)
    single_truth.to_csv(os.path.join(str(cik),f'{cik}_soi_table.csv'),index=False)
    
    
from utils import init_logger
init_logger()
main()

c:\Users\pysol\Desktop\projects\sec_filings\sec_windows\lib\site-packages\fuzzywuzzy\fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')
C:\Users\pysol\AppData\Local\Temp\ipykernel_12996\1652482565.py:177: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data


2012-06-30
C:\Users\pysol\Desktop\projects\sec_filings\1370755\2012-06-30\Schedule_of_Investments_1.csv
C:\Users\pysol\Desktop\projects\sec_filings\1370755\2012-06-30\Schedule_of_Investments_2.csv


C:\Users\pysol\AppData\Local\Temp\ipykernel_12996\1652482565.py:177: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data
C:\Users\pysol\AppData\Local\Temp\ipykernel_12996\1652482565.py:177: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data
C:\Users\pysol\AppData\Local\Temp\ipykernel_12996\1652482565.py:177: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the ca

C:\Users\pysol\Desktop\projects\sec_filings\1370755\2012-06-30\Schedule_of_Investments_3.csv
C:\Users\pysol\Desktop\projects\sec_filings\1370755\2012-06-30\Schedule_of_Investments_4.csv


C:\Users\pysol\AppData\Local\Temp\ipykernel_12996\1652482565.py:188: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  lambda row: re.search('|'.join(company_control_headers() if control else common_subheaders()), str(row[0]), re.IGNORECASE) is not None,
C:\Users\pysol\AppData\Local\Temp\ipykernel_12996\1652482565.py:177: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data
C:\Users\pysol\AppData\Local\Temp\ipykernel_12996\1652482565.py:177: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc

...

C:\Users\pysol\AppData\Local\Temp\ipykernel_12996\1652482565.py:177: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data


C:\Users\pysol\Desktop\projects\sec_filings\1370755\2024-03-31\Schedule_of_Investments_9.csv


C:\Users\pysol\AppData\Local\Temp\ipykernel_12996\1652482565.py:177: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data


C:\Users\pysol\Desktop\projects\sec_filings\1370755\2024-03-31\Schedule_of_Investments_10.csv


C:\Users\pysol\AppData\Local\Temp\ipykernel_12996\1652482565.py:177: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data
C:\Users\pysol\AppData\Local\Temp\ipykernel_12996\1652482565.py:188: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  lambda row: re.search('|'.join(company_control_headers() if control else common_subheaders()), str(row[0]), re.IGNORECASE) is not None,
C:\Users\pysol\AppData\Local\Temp\ipykernel_12996\1652482565.py:188: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer k

In [232]:
def _clean(
    file_path:str,
    regex_pattern:str=r'\w+\s+\d{1,2},\s+\d{4}',
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0,na_values=[' ', ''])
        
    df.replace(['\u200b',None, r'^\s*$'],np.nan,regex=True,inplace=True) #':','$','%'
    df.dropna(axis=0,how='all',inplace=True)
    
    df = df[~df.apply(lambda row:row.astype(str).str.match(regex_pattern).all(),axis=1)]
    important_fields,idx = get_key_fields(df)
    df.columns = important_fields
    df = merge_duplicate_columns(df).reset_index(drop=True)
    
    duplicate_idx = df.apply(lambda row:(row != np.nan).duplicated().sum() > 7 ,axis=1)
    df.loc[duplicate_idx] = df.loc[duplicate_idx].apply(remove_row_duplicates, axis=1)
    
    df.replace([r'^\s*$'],np.nan,regex=True,inplace=True) #':','$','%'
    df.dropna(axis=1,how='all',inplace=True)
    
    columns = (~df.isna()).sum(axis=0) <= 3
    df.drop(columns=df.columns[columns],inplace=True)
    return df.reset_index(drop=True)


file_path = r'C:\Users\pysol\Desktop\projects\sec_filings\1370755\2020-03-31\Schedule_of_Investments_8.csv'
df = _clean(file_path)
index_list = df.apply(
    lambda row:row.astype(str).str.contains(stopping_criterion(), case=False, na=False).any(),
    axis=1
)
index_list_sum = index_list.sum()
index_list_sum

1

In [233]:
df

Issuer  \
0                                              Issuer   
1                       Equity Securities (continued)   
2                                               Media   
3          NEG Parent, LLC (Core Entertainment, Inc.)   
4          NEG Parent, LLC (Core Entertainment, Inc.)   
5          NEG Parent, LLC (Core Entertainment, Inc.)   
6                                         Quora, Inc.   
7                       Shop Holding, LLC (Connexity)   
8                   SoundCloud, Ltd. (United Kingdom)   
9                                                 NaN   
10                      Oil, Gas and Consumable Fuels   
11                 Iracore Investments Holdings, Inc.   
12                              Professional Services   
13                                      Anacomp, Inc.   
14         Semiconductors and Semiconductor Equipment   
15                    Adesto Technologies Corporation   
16                                      Nanosys, Inc.   
17                                                NaN   
18                                           Software   
19                                      Actifio, Inc.   
20                                   Tradeshift, Inc.   
21                                                NaN   
22     Total Equity Securities - 15.3% of Nets Assets   
23           Total Investments - 239.3% of Net Assets   
24                          Cash and Cash Equivalents   
25       Cash Held on Account at Various Institutions   
26                          Cash and Cash Equivalents   
27  Total Cash and Investments - 240.5% of Net Assets   

                                                 rate footnotes  \
0                                          Expiration     Notes   
1                                                 NaN       NaN   
2                                                 NaN       NaN   
3                                                 NaN   B/C/E/N   
4                                          10/17/2026   B/C/E/N   
5                                          10/17/2026   B/C/E/N   
6                                           4/11/2029     C/E/N   
7                                                 NaN     C/E/N   
8                                           4/29/2025   C/E/H/N   
9                                                 NaN       NaN   
10                                                NaN       NaN   
11                                                NaN   B/C/E/N   
12                                                NaN       NaN   
13                                                NaN   C/E/F/N   
14                                                NaN       NaN   
15                                           5/8/2024     C/E/N   
16                                          3/29/2023     C/E/N   
17                                                NaN       NaN   
18                                                NaN       NaN   
19                                           5/5/2027     C/E/N   
20                                          3/26/2027     C/E/N   
21                                                NaN       NaN   
22     Total Equity Securities - 15.3% of Nets Assets       NaN   
23           Total Investments - 239.3% of Net Assets       NaN   
24                          Cash and Cash Equivalents       NaN   
25                                                NaN       NaN   
26                          Cash and Cash Equivalents       NaN   
27  Total Cash and Investments - 240.5% of Net Assets         M   

                                                       \
0                                                 NaN   
1                                                 NaN   
2                                               Media   
3                                                 NaN   
4                                                 NaN   
5                                                 NaN   
6                                                 

# cik==1326003

In [8]:
import os
import re
import glob
import logging
import datetime
import pandas as pd
import numpy as np
from bs4 import BeautifulSoup
from fuzzywuzzy import process

'''
TO DO 
separate issuer investment
make issuer would have company name

June 30 2021

start Black rock capital investment core BKCC (cik==1326003)
'''
# https://www.sec.gov/robots.txt
def get_standard_name(col, choices, score_cutoff=60):
    best_match, score = process.extractOne(col, choices)
    if score > score_cutoff:
        return best_match
    return col

def stopping_criterion()->str:
    return '{}'.format(r'Total\s*Investments')

def exceptions(bdc:str)->list:
    return [
        os.path.join(bdc,'2015-03-31\Schedule_of_Investments_4.csv'),
        os.path.join(bdc,'2015-03-31\Schedule_of_Investments_1.csv'),
        os.path.join(bdc,'2015-03-31\Schedule_of_Investments_7.csv'),
        os.path.join(bdc,'2015-03-31\Schedule_of_Investments_10.csv'),
        os.path.join(bdc,'2015-06-30\Schedule_of_Investments_1.csv'),
        os.path.join(bdc,'2015-06-30\Schedule_of_Investments_4.csv'),
        os.path.join(bdc,'2015-06-30\Schedule_of_Investments_7.csv'),
        os.path.join(bdc,'2015-06-30\Schedule_of_Investments_10.csv'),
    ]

def concat(*dfs)->list:
    final = []
    for df in dfs:
        final.extend(df.values.tolist())
    return final

def common_subheaders()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        ('Advertising, Public Relations and Marketing ',
        'Air Transportation',
        'Amusement and Recreation',
        'Apparel Manufacturing',
        'Building Equipment Contractors',
        'Business Support Services',
        'Chemicals',
        'Communications Equipment Manufacturing',
        'Credit Related Activities',
        'Computer Systems Design and Related Services',
        'Credit (Nondepository)',
        'Data Processing and Hosting Services',
        'Educational Support Services',
        'Electronic Component Manufacturing',
        'Equipment Leasing',
        'Facilities Support Services',
        'Grocery Stores',
        'Hospitals',
        'Insurance',
        'Lessors of Nonfinancial Licenses',
        'Management, Scientific, and Technical Consulting Services',
        'Motion Picture and Video Industries',
        'Other Information Services',
        'Other Manufacturing',
        'Other Publishing',
        'Other Real Estate Activities',
        'Other Telecommunications',
        'Plastics Manufacturing',
        'Radio and Television Broadcasting',
        'Real Estate Leasing',
        'Restaurants',
        'Retail',
        'Satellite Telecommunications',
        'Scientific Research and Development Services',
        'Texttile Furnishings Mills',
        'Traveler Arrangement',
        'Software Publishing',
        'Utility System Construction',
        'Wholesalers',
        'Wired Telecommunications Carriers',
        'Wireless Telecommunications Carriers',
        )
    ))

def standard_field_names()->tuple:
    return (
        'portfolio',
        'footnotes',
        'industry',
        'rate',
        'floor',
        'maturity',
        'principal amount', # TODO change stand names for more dynamic fuzzywuzzy matching
        'cost',
        'fair value',
        'investment',
        'date',
        'subheaders',
        'number of shares',
        'of net assets',
        'type',
        'effective yield',
        'share units',
        'Percent of Case and Investments',
        '\\% of Portfolio',
        'issuer'
    )

def company_control_headers()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        (
        'Debt Investments',
        'Debt Investments (82.23%)',
        'Debt Investments (A)',
        'Debt Investments (continued)',
        'Equity Securities',
        'Equity Securities (continued)',
        'Cash and Cash Equivalents',
        )
    ))

def strip_string(
    columns_names:list,
    standardize:bool=False
)->tuple:
    # columns = tuple(map(lambda col:re.sub(r'[^a-z]', '', str(col).lower()),columns_names))
    if standardize:
        standard_fields = standard_field_names()
        return tuple(
            re.sub(r'\s+', '_',get_standard_name(col,standard_fields)) for col in columns_names
        )
    return tuple(re.sub(r'\s+', '_',col) for col in columns_names)

def get_key_fields(
    df_cur:pd.DataFrame
)->tuple:
    important_fields = standard_field_names() + common_subheaders()
    for idx,row in enumerate(df_cur.iterrows()):
        found = any(any(
            key in str(field).lower() 
            for key in important_fields)
                    for field in row[-1].dropna().tolist()
            )
        if found and len(set(row[-1].dropna().tolist())) >= 4:
            cols = df_cur.iloc[:idx + 1].apply(lambda row: ' '.join(row.dropna()), axis=0).tolist()
            fields = strip_string(cols,standardize=found) ,idx
            return fields
    return strip_string(df_cur.iloc[0].tolist(),standardize=found),0


# Function to extract date and convert to datetime object
def extract_date(file_path):
    # Extract date from file path (assuming date is always in 'YYYY-MM-DD' format)
    date_str = re.search(r'\d{4}-\d{2}-\d{2}', file_path).group()
    return datetime.datetime.strptime(date_str, '%Y-%m-%d')

def remove_row_duplicates(row):
    seen = set()
    return pd.Series([x if x not in seen and not seen.add(x) else None for x in row])


def merge_duplicate_columns(
    df:pd.DataFrame,
)->pd.DataFrame:
    duplicate_cols = df.columns[df.columns.duplicated(keep=False)]
    for col_name in duplicate_cols.unique():
        duplicate_data = df.loc[:, df.columns == col_name]
        merged_data = duplicate_data.apply(lambda row: ' '.join(set(row.dropna().astype(str))), axis=1)
        df = df.loc[:, df.columns != col_name]
        df[col_name] = merged_data
    return df

def extract_subheaders(
    df:pd.DataFrame,
    control:bool,
)->pd.DataFrame:
    col_name = 'company_control' if control else 'Type_of_Investment'
    if col_name in df.columns:
        return df
    include = df.apply(
        lambda row: re.search('|'.join(company_control_headers() if control else common_subheaders()), str(row[0]), re.IGNORECASE) is not None,
        axis=1
    )  
    
    exclude = ~df.apply(
        lambda row: row.astype(str).str.contains('total|Inc|Ltd|LLC|Holdings|LP|Co|Corporation', case=False, na=False).any(),
        axis=1
    )
    idx = df[include & exclude].index.tolist()
    df[col_name] = None
    if not idx:
        return df

    prev_header = subheader = None
    df.loc[idx[-1]:,col_name] = df.iloc[idx[-1],1] if isinstance(df.iloc[idx[-1],0],float)  else df.iloc[idx[-1],0]
    for j,i in enumerate(idx[:-1]):
        prev_header = subheader
        subheader = df.iloc[i,1] if isinstance(df.iloc[i,0],float)  else df.iloc[i,0]
        df.loc[idx[j]:idx[j+1],col_name] = subheader if subheader != '' else prev_header
    return df

def _clean(
    file_path:str,
    regex_pattern:str=r'\w+\s+\d{1,2},\s+\d{4}',
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0,na_values=[' ', ''])
        
    df.replace(['\u200b',None, r'^\s*$'],np.nan,regex=True,inplace=True) #':','$','%'
    df.dropna(axis=0,how='all',inplace=True)
    
    df = df[~df.apply(lambda row:row.astype(str).str.match(regex_pattern).all(),axis=1)]
    important_fields,idx = get_key_fields(df)
    df.columns = important_fields
    df = merge_duplicate_columns(df).reset_index(drop=True)
    
    duplicate_idx = df.apply(lambda row:(row != np.nan).duplicated().sum() > 7 ,axis=1)
    df.loc[duplicate_idx] = df.loc[duplicate_idx].apply(remove_row_duplicates, axis=1)
    
    df.replace([r'^\s*$'],np.nan,regex=True,inplace=True) #':','$','%'
    df.dropna(axis=1,how='all',inplace=True)
    
    columns = (~df.isna()).sum(axis=0) <= 3
    df.drop(columns=df.columns[columns],inplace=True)
    return df.reset_index(drop=True)

def md_parse(
    xml_file:str
):
    # Load HTML content
    with open(xml_file, 'r') as file:
        html_content = file.read()
    soup = BeautifulSoup(html_content, 'html.parser')
    # If the content is inside <pre>, get the text within it
    pre_text = soup.find('pre').get_text()
    # print(pre_text)
    start = pre_text.split('Portfolio Company')[-1]
    if start == pre_text:
        start = pre_text.split('PORTFOLIO COMPANY')[-1]

    start = 'Portfolio Company' + start[:len(start)]
    end = start.split('NET ASSETS')[0]
    # print(end)
    lines = end.split('\n')
    data = []
    num_cols = len(lines[0].split())
    for line in lines:
        line = line.replace('$','')
        row = [np.nan]*num_cols
        values = re.split(r'\s{4,}', line)
        row[:len(values)] = values
        data.append(row)   

    df = pd.DataFrame(data,columns=data[0]).dropna(axis=1,how='all')
    important_fields,idx = get_key_fields(df)
    df.columns = important_fields
    return df

cik = 1326003
ROOT_PATH = r'C:\Users\pysol\Desktop\projects\sec_filings'

def main()->None:
    bdc = os.path.join(ROOT_PATH,str(cik))
    qtrs = os.listdir(bdc)
    stop = stopping_criterion()
    for qtr in qtrs:
        if qtr in ['2005-09-30','2005-12-31','2006-03-31','2006-06-30','2006-09-30']:
            if not os.path.exists(os.path.join(bdc,qtr,'output')):
                os.mkdir(os.path.join(bdc,qtr,'output'))
            f = os.listdir(os.path.join(bdc,qtr))[0]
            df = md_parse(os.path.join(bdc,qtr,f))
            df['qtr'] = qtr.split('\\')[-1]
            df.to_csv(f"{os.path.join(bdc,qtr,'output',qtr)}.csv",index=False)
            continue
        
        if '.csv' in qtr or not os.path.exists(os.path.join(bdc,qtr,f'Schedule_of_Investments_0.csv')):
            continue
        # qtr = '2005-09-30'
        print(qtr)

        index_list_sum = i = 0
        soi_files = sorted([
            os.path.join(bdc,qtr,file) 
            for file in os.listdir(os.path.join(bdc,qtr))
            if '.csv' in file
        ],key=lambda f: int(f.split('_')[-1].split('.')[0]))
        df = _clean(soi_files[i])
        index_list = df.apply(
            lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
            axis=1
        )
        index_list_sum = index_list.sum()
        dfs = [df]     
        i += 1
        cols = df.columns.tolist()
        while index_list_sum == 0 :
            print(soi_files[i])
            df = _clean(soi_files[i])
            if set(list(range(10))) >= set(df.columns.tolist()):
                df.columns = cols
            dfs.append(df)
            index_list = df.apply(
                lambda row:row.astype(str).str.contains(stop, case=False, na=False).any(),
                axis=1
            )
            index_list_sum = index_list.sum()
            i += 1
            
        date_final = dfs[0]
        if len(dfs) > 1:
            date_final = pd.concat(dfs,axis=0,ignore_index=True)#pd.DataFrame(concat(*dfs))
        date_final = extract_subheaders(date_final,control=True)
        date_final = extract_subheaders(date_final,control=False)

        date_final['qtr'] = qtr.split('\\')[-1]
        if not os.path.exists(os.path.join(bdc,qtr,'output')):
            os.makedirs(os.path.join(bdc,qtr,'output'))
        columns_to_drop = date_final.notna().sum() <= 2
        date_final.drop(columns=columns_to_drop[columns_to_drop].index)
        date_final.to_csv(os.path.join(bdc,qtr,'output',f'{qtr}.csv'),index=False)
        # break
    # Use glob to find files
    files = sorted(glob.glob(f'{cik}/*/output/*.csv'), key=extract_date)
    single_truth = pd.concat([
        pd.read_csv(df) for df in files
    ],axis=0,ignore_index=True)
    single_truth.drop(columns=single_truth.columns[['Unnamed' in col for col in single_truth.columns]],inplace=True)
    single_truth.to_csv(os.path.join(str(cik),f'{cik}_soi_table.csv'),index=False)
    
    
from utils import init_logger
init_logger()
main()
# can cut markdown 2005 - 2006

2006-12-31
C:\Users\pysol\Desktop\projects\sec_filings\1326003\2006-12-31\Schedule_of_Investments_1.csv
C:\Users\pysol\Desktop\projects\sec_filings\1326003\2006-12-31\Schedule_of_Investments_2.csv
C:\Users\pysol\Desktop\projects\sec_filings\1326003\2006-12-31\Schedule_of_Investments_3.csv
C:\Users\pysol\Desktop\projects\sec_filings\1326003\2006-12-31\Schedule_of_Investments_4.csv


C:\Users\pysol\AppData\Local\Temp\ipykernel_17816\1629857662.py:179: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data
C:\Users\pysol\AppData\Local\Temp\ipykernel_17816\1629857662.py:179: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data
C:\Users\pysol\AppData\Local\Temp\ipykernel_17816\1629857662.py:179: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the ca

2007-03-31
C:\Users\pysol\Desktop\projects\sec_filings\1326003\2007-03-31\Schedule_of_Investments_1.csv
C:\Users\pysol\Desktop\projects\sec_filings\1326003\2007-03-31\Schedule_of_Investments_2.csv
C:\Users\pysol\Desktop\projects\sec_filings\1326003\2007-03-31\Schedule_of_Investments_3.csv


C:\Users\pysol\AppData\Local\Temp\ipykernel_17816\1629857662.py:179: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data
C:\Users\pysol\AppData\Local\Temp\ipykernel_17816\1629857662.py:179: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data
C:\Users\pysol\AppData\Local\Temp\ipykernel_17816\1629857662.py:179: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the ca

C:\Users\pysol\Desktop\projects\sec_filings\1326003\2007-03-31\Schedule_of_Investments_4.csv
2007-06-30
C:\Users\pysol\Desktop\projects\sec_filings\1326003\2007-06-30\Schedule_of_Investments_1.csv
C:\Users\pysol\Desktop\projects\sec_filings\1326003\2007-06-30\Schedule_of_Investments_2.csv
C:\Users\pysol\Desktop\projects\sec_filings\1326003\2007-06-30\Schedule_of_Investments_3.csv


...

C:\Users\pysol\AppData\Local\Temp\ipykernel_17816\1629857662.py:179: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data
C:\Users\pysol\AppData\Local\Temp\ipykernel_17816\1629857662.py:179: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data


C:\Users\pysol\Desktop\projects\sec_filings\1326003\2023-12-31\Schedule_of_Investments_4.csv
C:\Users\pysol\Desktop\projects\sec_filings\1326003\2023-12-31\Schedule_of_Investments_5.csv


C:\Users\pysol\AppData\Local\Temp\ipykernel_17816\1629857662.py:179: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data
C:\Users\pysol\AppData\Local\Temp\ipykernel_17816\1629857662.py:179: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data


C:\Users\pysol\Desktop\projects\sec_filings\1326003\2023-12-31\Schedule_of_Investments_6.csv


C:\Users\pysol\AppData\Local\Temp\ipykernel_17816\1629857662.py:179: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col_name] = merged_data
C:\Users\pysol\AppData\Local\Temp\ipykernel_17816\1629857662.py:228: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df.replace([r'^\s*$'],np.nan,regex=True,inplace=True) #':','$','%'
C:\Users\pysol\AppData\Local\Temp\ipykernel_17816\1629857662.py:190: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treate

In [1]:
def _clean(
    file_path:str,
    regex_pattern:str=r'\w+\s+\d{1,2},\s+\d{4}',
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0,na_values=[' ', ''])
        
    df.replace(['\u200b',None, r'^\s*$'],np.nan,regex=True,inplace=True) #':','$','%'
    df.dropna(axis=0,how='all',inplace=True)
    
    df = df[~df.apply(lambda row:row.astype(str).str.match(regex_pattern).all(),axis=1)]
    important_fields,idx = get_key_fields(df)
    df.columns = important_fields
    df = merge_duplicate_columns(df).reset_index(drop=True)
    
    duplicate_idx = df.apply(lambda row:(row != np.nan).duplicated().sum() > 7 ,axis=1)
    df.loc[duplicate_idx] = df.loc[duplicate_idx].apply(remove_row_duplicates, axis=1)
    
    df.replace([r'^\s*$'],np.nan,regex=True,inplace=True) #':','$','%'
    df.dropna(axis=1,how='all',inplace=True)
    
    columns = (~df.isna()).sum(axis=0) <= 3
    df.drop(columns=df.columns[columns],inplace=True)
    return df.reset_index(drop=True)


file_path = r'C:\Users\pysol\Desktop\projects\sec_filings\1326003\2015-03-31\Schedule_of_Investments_4.csv'
df = _clean(file_path)
index_list = df.apply(
    lambda row:row.astype(str).str.contains(stopping_criterion(), case=False, na=False).any(),
    axis=1
)
index_list_sum = index_list.sum()
index_list_sum

NameError: name 'pd' is not defined

In [12]:
df

portfolio  \
0                                   Portfolio Company   
1                     Equity Warrants/Options—2.7%(c)   
2   Bankruptcy Management Solutions, Inc., Tranche...   
3   Bankruptcy Management Solutions, Inc., Tranche...   
4   Bankruptcy Management Solutions, Inc., Tranche...   
5                              Facet Investment, Inc.   
6                  Marsico Parent Superholdco, LLC(i)   
7                          New Gulf Resources, LLC(i)   
8   Oportun Financial Corporation (Progress Financ...   
9   Twin River Worldwide Holdings, Inc., Contingen...   
10                      Total Equity Warrants/Options   
11                           TOTAL INVESTMENTS—156.4%   
12           OTHER ASSETS & LIABILITIES (NET)—(56.4)%   
13                                  NET ASSETS—100.0%   

                                    industry  \
0                                   Industry   
1            Equity Warrants/Options—2.7%(c)   
2                        Financial  Services   
3                        Financial  Services   
4                        Financial  Services   
5                           Medical  Devices   
6                        Financial  Services   
7                                     Energy   
8                        Financial  Services   
9                                     Gaming   
10                                       NaN   
11                  TOTAL INVESTMENTS—156.4%   
12  OTHER ASSETS & LIABILITIES (NET)—(56.4)%   
13                                       NaN   

                                    maturity  \
0                                   Maturity   
1                                        NaN   
2                             expire 6/27/18   
3                             expire 6/27/19   
4                             expire 6/27/20   
5                             expire 1/18/21   
6                            expire 12/14/19   
7                              expire 5/9/24   
8                             expire various   
9                             expire 11/5/17   
10                                       NaN   
11                  TOTAL INVESTMENTS—156.4%   
12  OTHER ASSETS & LIABILITIES (NET)—(56.4)%   
13                                       NaN   

                                 principal_amount          cost  \
0   Principal  Amount or  Number of  Shares/Units       Cost(a)   
1                                             NaN           NaN   
2                                           28464      $375,040   
3                                           30654        342295   
4                                           45981        468803   
5                                            1978        250000   
6                                             455        444450   
7                                            4000        506505   
8                                         6959220       3183106   
9                                            1000          5000   
10                                            NaN       5575199   
11                                            NaN  $ 1114217610   
12       OTHER ASSETS & LIABILITIES (NET)—(56.4)%           NaN   
13                                            NaN           NaN   

        fair_value  
0   Fair  Value(b)  
1              NaN  
2         $687,690  
3           612160  
4           818922  
5                —  
6                —  
7                —  
8         18750614  
9           510000  
10        21379386  
11      1235636316  
12    (445,731,325  
13     789904991 $

In [29]:
from bs4 import BeautifulSoup
import pandas as pd
import re
import numpy as np





# xml_file = r'C:\Users\pysol\Desktop\projects\sec_filings\1326003\2005-09-30\brkcc10q.txt.html'
# xml_file = r'C:\Users\pysol\Desktop\projects\sec_filings\1326003\2005-12-31\brk10-k.txt.html'
# xml_file = r'C:\Users\pysol\Desktop\projects\sec_filings\1326003\2006-03-31\black10q.txt.html'
# xml_file = r'C:\Users\pysol\Desktop\projects\sec_filings\1326003\2006-06-30\blackjune30.txt.html'
xml_file = r'C:\Users\pysol\Desktop\projects\sec_filings\1326003\2006-09-30\bkcc10q906.txt.html'

def md_parse(
    xml_file:str
):
    # Load HTML content
    with open(xml_file, 'r') as file:
        html_content = file.read()
    soup = BeautifulSoup(html_content, 'html.parser')
    # If the content is inside <pre>, get the text within it
    pre_text = soup.find('pre').get_text()
    # print(pre_text)
    start = pre_text.split('Portfolio Company')[-1]
    if start == pre_text:
        start = pre_text.split('PORTFOLIO COMPANY')[-1]

    start = 'Portfolio Company' + start[:len(start)]
    end = start.split('NET ASSETS')[0]
    # print(end)
    lines = end.split('\n')
    data = []
    num_cols = len(lines[0].split())
    for line in lines:
        line = line.replace('$','')
        row = [np.nan]*num_cols
        values = re.split(r'\s{4,}', line)
        row[:len(values)] = values
        data.append(row)   

    return pd.DataFrame(data,columns=data[0]).dropna(axis=1,how='all')

md_parse(xml_file=xml_file)

Portfolio Company (a)                     Industry (b)  \
0                      Portfolio Company (a)                     Industry (b)   
1                          -----------------                         --------   
2                                        <S>                              <C>   
3                                                                         NaN   
4                    Closed-End Funds - 1.4%                              NaN   
5                                                                         NaN   
6     Eaton Vance Floating-Rate Income Trust                  Closed-End Fund   
7           Nuveen Floating Rate Income Fund                  Closed-End Fund   
8          PIMCO Floating Rate Strategy Fund                  Closed-End Fund   
9                                             --------------- ---------------   
10                    Total Closed-End Funds                        7,144,581   
11                                            --------------- ---------------   
12                                                                        NaN   
13                Equity Warrants - 0.0% (g)                              NaN   
14                                                                        NaN   
15      ATEP Holdings, Inc., expire 10/24/15                Plastic Packaging   
16                                                                        NaN   
17       ATH Holdings, Inc., expire 10/24/15                Plastic Packaging   
18      ATPP Holdings, Inc., expire 10/24/15                Plastic Packaging   
19      ATPR Holdings, Inc., expire 10/24/15                Plastic Packaging   
20                                            --------------- ---------------   
21                     Total Equity Warrants                           90,114   
22                                            --------------- ---------------   
23                                                                        NaN   
24               TOTAL LONG-TERM INVESTMENTS                              NaN   
25                 INCLUDING UNEARNED INCOME                      144,696,981   
26                                                                        NaN   
27                  UNEARNED INCOME - (0.2)%                        (887,949)   
28                                                                        NaN   
29               TOTAL LONG-TERM INVESTMENTS                      143,809,032   
30                                            --------------- ---------------   
31                                                                        NaN   
32                 TOTAL INVESTMENTS - 47.4%                      250,184,074   
33                                            =============== ---------------   
34                                                                        NaN   
35  OTHER ASSETS & LIABILITIES (NET) - 52.6%                      278,268,499   
36                                                            ---------------   
37                                                                        NaN   
38                                                                        NaN   

                                       Shares/Units   Cost (c)       Value  
0                                      Shares/Units   Cost (c)       Value  
1   --------------- --------------- ---------------        NaN         NaN  
2                                               <C>        <C>         <C>  
3                                               NaN        NaN         NaN  
4                                               NaN        NaN         NaN  
5                                               NaN        NaN         NaN  
6                                           175,000  2,988,408   2,952,250  
7                                            94,400  1,159,147   1,188,496  
8                                           170,000  2,997,026   3,036,200  
9           

# cik 1580345

In [96]:
import os
import re
import glob
import logging
import datetime
import pandas as pd
import numpy as np
from bs4 import BeautifulSoup
from fuzzywuzzy import process

'''
TO DO 
separate issuer investment
make issuer would have company name

June 30 2021

start Black rock capital investment core BKCC (cik==1326003)
'''
# https://www.sec.gov/robots.txt
def get_standard_name(col, choices, score_cutoff=60):
    best_match, score = process.extractOne(col, choices)
    if score > score_cutoff:
        return best_match
    return col

def stopping_criterion(qtr:str)->str:
    if qtr == '2023-12-31':
        return '{}'.format(r'Total\s*Cash\s*Equivalents')
    return '{}'.format(r'Total\s*Investments')

def exceptions(bdc:str)->list:
    return [
        os.path.join(bdc,'2015-03-31\Schedule_of_Investments_4.csv'),
        os.path.join(bdc,'2015-03-31\Schedule_of_Investments_1.csv'),
        os.path.join(bdc,'2015-03-31\Schedule_of_Investments_7.csv'),
        os.path.join(bdc,'2015-03-31\Schedule_of_Investments_10.csv'),
        os.path.join(bdc,'2015-06-30\Schedule_of_Investments_1.csv'),
        os.path.join(bdc,'2015-06-30\Schedule_of_Investments_4.csv'),
        os.path.join(bdc,'2015-06-30\Schedule_of_Investments_7.csv'),
        os.path.join(bdc,'2015-06-30\Schedule_of_Investments_10.csv'),
    ]

def concat(*dfs)->list:
    final = []
    for df in dfs:
        final.extend(df.values.tolist())
    return final

def common_subheaders()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        ('Advertising, Public Relations and Marketing ',
        'Air Transportation',
        'Amusement and Recreation',
        'Apparel Manufacturing',
        'Building Equipment Contractors',
        'Business Support Services',
        'Chemicals',
        'Communications Equipment Manufacturing',
        'Credit Related Activities',
        'Computer Systems Design and Related Services',
        'Credit (Nondepository)',
        'Data Processing and Hosting Services',
        'Educational Support Services',
        'Electronic Component Manufacturing',
        'Equipment Leasing',
        'Facilities Support Services',
        'Grocery Stores',
        'Hospitals',
        'Insurance',
        'Lessors of Nonfinancial Licenses',
        'Management, Scientific, and Technical Consulting Services',
        'Motion Picture and Video Industries',
        'Other Information Services',
        'Other Manufacturing',
        'Other Publishing',
        'Other Real Estate Activities',
        'Other Telecommunications',
        'Plastics Manufacturing',
        'Radio and Television Broadcasting',
        'Real Estate Leasing',
        'Restaurants',
        'Retail',
        'Satellite Telecommunications',
        'Scientific Research and Development Services',
        'Texttile Furnishings Mills',
        'Traveler Arrangement',
        'Software Publishing',
        'Utility System Construction',
        'Wholesalers',
        'Wired Telecommunications Carriers',
        'Wireless Telecommunications Carriers',
        )
    ))

def standard_field_names()->tuple:
    return (
        'portfolio',
        'footnotes',
        'industry',
        'rate',
        'floor',
        'maturity',
        'principal amount', # TODO change stand names for more dynamic fuzzywuzzy matching
        'cost',
        'fair value',
        'investment',
        'date',
        'subheaders',
        'number of shares',
        'of net assets',
        'type',
        'effective yield',
        'share units',
        'Percent of Case and Investments',
        '\\% of Portfolio',
        'issuer'
    )

def company_control_headers()->tuple:
    return tuple(map(lambda header:header.replace(' ', r'\s*'),
        (
        'Debt Investments',
        'Debt Investments (82.23%)',
        'Debt Investments (A)',
        'Debt Investments (continued)',
        'Equity Securities',
        'Equity Securities (continued)',
        'Cash and Cash Equivalents',
        )
    ))

def strip_string(
    columns_names:list,
    standardize:bool=False
)->tuple:
    # columns = tuple(map(lambda col:re.sub(r'[^a-z]', '', str(col).lower()),columns_names))
    if standardize:
        standard_fields = standard_field_names()
        return tuple(
            re.sub(r'\s+', '_',get_standard_name(col,standard_fields)) for col in columns_names
        )
    return tuple(re.sub(r'\s+', '_',col) for col in columns_names)

def get_key_fields(
    df_cur:pd.DataFrame
)->tuple:
    important_fields = standard_field_names() + common_subheaders()
    for idx,row in enumerate(df_cur.iterrows()):
        found = any(any(
            key in str(field).lower() 
            for key in important_fields)
                    for field in row[-1].dropna().tolist()
            )
        if found and len(set(row[-1].dropna().tolist())) >= 4:
            cols = df_cur.iloc[:idx + 1].apply(lambda row: ' '.join(row.dropna()), axis=0).tolist()
            fields = strip_string(cols,standardize=found) ,idx
            return fields
    return strip_string(df_cur.iloc[0].tolist(),standardize=found),0


# Function to extract date and convert to datetime object
def extract_date(file_path):
    # Extract date from file path (assuming date is always in 'YYYY-MM-DD' format)
    date_str = re.search(r'\d{4}-\d{2}-\d{2}', file_path).group()
    return datetime.datetime.strptime(date_str, '%Y-%m-%d')


def merge_duplicate_columns(
    df:pd.DataFrame,
)->pd.DataFrame:
    duplicate_cols = df.columns[df.columns.duplicated(keep=False)]
    for col_name in duplicate_cols.unique():
        duplicate_data = df.loc[:, df.columns == col_name]
        merged_data = duplicate_data.apply(lambda row: ' '.join(set(row.dropna().astype(str))), axis=1)
        df = df.loc[:, df.columns != col_name]
        df[col_name] = merged_data
    return df

def extract_subheaders(
    df:pd.DataFrame,
    control:bool,
)->pd.DataFrame:
    col_name = 'company_control' if control else 'Type_of_Investment'
    if col_name in df.columns:
        return df
    include = df.apply(
        lambda row: re.search('|'.join(company_control_headers() if control else common_subheaders()), str(row[0]), re.IGNORECASE) is not None,
        axis=1
    )  
    
    exclude = ~df.apply(
        lambda row: row.astype(str).str.contains('total|Inc|Ltd|LLC|Holdings|LP|Co|Corporation', case=False, na=False).any(),
        axis=1
    )
    idx = df[include & exclude].index.tolist()
    df[col_name] = None
    if not idx:
        return df

    prev_header = subheader = None
    df.loc[idx[-1]:,col_name] = df.iloc[idx[-1],1] if isinstance(df.iloc[idx[-1],0],float)  else df.iloc[idx[-1],0]
    for j,i in enumerate(idx[:-1]):
        prev_header = subheader
        subheader = df.iloc[i,1] if isinstance(df.iloc[i,0],float)  else df.iloc[i,0]
        df.loc[idx[j]:idx[j+1],col_name] = subheader if subheader != '' else prev_header
    return df


def remove_row_duplicates(row:pd.Series)->pd.Series: 
    out = []
    for v in row:
        if v in out:
            out.append(np.nan)
        else:
            out.append(v)
    return pd.Series(out)

def remove_regex(qtr:str)->tuple:
    if qtr == "2019-12-31":
        return re.compile(r"TRIPLEPOINT VENTURE GROWTH BDC CORP\. AND SUBSIDIARIES\s+CONSOLIDATED SCHEDULE OF INVESTMENTS\s+\(in thousands\)\s+(?:\(unaudited\)\s+)?As of\s+\w+\s+\d{1,2},?\s+\d{4}")
    if qtr == '2020-12-31':
        return re.compile(r"TRIPLEPOINT VENTURE GROWTH BDC CORP\. AND SUBSIDIARIES\s+CONSOLIDATED SCHEDULE OF INVESTMENTS\s+\(dollars in thousands\)\s+As of\s+\w+\s+\d{1,2},?\s+\d{4}")
    if qtr == "2021-12-31":
        return re.compile(r"TRIPLEPOINT VENTURE GROWTH BDC CORP\. AND SUBSIDIARIES\s+CONSOLIDATED SCHEDULE OF INVESTMENTS\s+\(dollars in thousands\)\s+As of\s+\w+\s+\d{1,2},?\s+\d{4}")
    if qtr == '2022-12-31':
        return re.compile(r"TRIPLEPOINT VENTURE GROWTH BDC CORP\. AND SUBSIDIARIES\s+CONSOLIDATED SCHEDULE OF INVESTMENTS\s+\(dollars in thousands\)\s+(?:\(unaudited\)\s+)?As of\s+\w+\s+\d{1,2},?\s+\d{4}")
    if qtr in ['2023-06-30','2023-09-30','2023-12-31']:
        return re.compile(r"TRIPLEPOINT VENTURE GROWTH BDC CORP\. AND SUBSIDIARIES\s+CONSOLIDATED SCHEDULE OF INVESTMENTS\s+\(dollars in thousands\)\s+(\(unaudited\)\s+)?As of\s+\w+\s+\d{1,2},\s+\d{4}")
    return re.compile(r"^TRIPLEPOINT VENTURE GROWTH BDC CORP\. AND SUBSIDIARIES\s+CONSOLIDATED SCHEDULE OF INVESTMENTS\s+\((unaudited|dollars in thousands|in thousands)\)\s+\((unaudited|dollars in thousands|in thousands)\)?\s+As of (January|February|March|April|May|June|July|August|September|October|November|December) \d{1,2}, \d{4}$|TRIPLEPOINT\s+VENTURE\s+GROWTH\s+BDC\s+CORP\.\s+AND\s+SUBSIDIARIES\s+CONSOLIDATED\s+SCHEDULE\s+OF\s+INVESTMENTS\s+\(dollars\s+in\s+thousands\)\s+\(unaudited\)\s+As\s+of\s+March\s+31,\s+2023|TRIPLEPOINT\s+VENTURE\s+GROWTH\s+BDC\s+CORP\.\s+AND\s+SUBSIDIARIES\s+CONSOLIDATED\s+SCHEDULE\s+OF\s+INVESTMENTS\s+\(unaudited\)\s+\(dollars\s+in\s+thousands\)\s+As\s+of\s+March\s+31,\s+2024")
    
def _clean(
    file_path:str,
    regex_pattern:str=r"^TRIPLEPOINT VENTURE GROWTH BDC CORP\. AND SUBSIDIARIES\s+CONSOLIDATED SCHEDULE OF INVESTMENTS\s+\((unaudited|dollars in thousands|in thousands)\)\s+\((unaudited|dollars in thousands|in thousands)\)?\s+As of (January|February|March|April|May|June|July|August|September|October|November|December) \d{1,2}, \d{4}$|TRIPLEPOINT\s+VENTURE\s+GROWTH\s+BDC\s+CORP\.\s+AND\s+SUBSIDIARIES\s+CONSOLIDATED\s+SCHEDULE\s+OF\s+INVESTMENTS\s+\(dollars\s+in\s+thousands\)\s+\(unaudited\)\s+As\s+of\s+March\s+31,\s+2023|TRIPLEPOINT\s+VENTURE\s+GROWTH\s+BDC\s+CORP\.\s+AND\s+SUBSIDIARIES\s+CONSOLIDATED\s+SCHEDULE\s+OF\s+INVESTMENTS\s+\(unaudited\)\s+\(dollars\s+in\s+thousands\)\s+As\s+of\s+March\s+31,\s+2024"
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0,na_values=[' ', ''])
        
    df.replace(['\u200b',None, r'^\s*$'],np.nan,regex=True,inplace=True) #':','$','%'
    df.dropna(axis=0,how='all',inplace=True)
    
    df = df[~df.apply(lambda row:row.astype(str).str.match(regex_pattern).all(),axis=1)]
    important_fields,idx = get_key_fields(df)
    df.columns = important_fields
    df = merge_duplicate_columns(df).reset_index(drop=True)
    
    duplicate_idx = df.apply(lambda row:row[pd.to_numeric(row,errors='coerce').isna()].duplicated().sum() > 1 ,axis=1)
    clean_rows = df.loc[duplicate_idx].apply(remove_row_duplicates, axis=1).reset_index(drop=True)
    j = 0
    for i,flag in enumerate(duplicate_idx):
        if not flag:
            continue
        df.iloc[i,:] = clean_rows.loc[j,:]
        j += 1
    df.replace([r'^\s*$'],np.nan,regex=True,inplace=True) #':','$','%'
    df.dropna(axis=1,how='all',inplace=True)
    
    columns = (~df.isna()).sum(axis=0) <= 3 
    df.drop(columns=df.columns[columns],inplace=True)
    return df.reset_index(drop=True)

def md_parse(
    xml_file:str
):
    # Load HTML content
    with open(xml_file, 'r') as file:
        html_content = file.read()
    soup = BeautifulSoup(html_content, 'html.parser')
    # If the content is inside <pre>, get the text within it
    pre_text = soup.find('pre').get_text()
    # print(pre_text)
    start = pre_text.split('Portfolio Company')[-1]
    if start == pre_text:
        start = pre_text.split('PORTFOLIO COMPANY')[-1]

    start = 'Portfolio Company' + start[:len(start)]
    end = start.split('NET ASSETS')[0]
    # print(end)
    lines = end.split('\n')
    data = []
    num_cols = len(lines[0].split())
    for line in lines:
        line = line.replace('$','')
        row = [np.nan]*num_cols
        values = re.split(r'\s{4,}', line)
        row[:len(values)] = values
        data.append(row)   

    df = pd.DataFrame(data,columns=data[0]).dropna(axis=1,how='all')
    important_fields,idx = get_key_fields(df)
    df.columns = important_fields
    return df

def exceptions()->tuple:
    return (
        '2015-03-31\Schedule_of_Investments_4.csv',
        '2014-12-31\Schedule_of_Investments_5.csv'
    )

cik = 1580345
ROOT_PATH = r'C:\Users\pysol\Desktop\projects\sec_filings'

def main()->None:
    bdc = os.path.join(ROOT_PATH,str(cik))
    qtrs = os.listdir(bdc)
    for qtr in qtrs:
        if '.csv' in qtr or not os.path.exists(os.path.join(bdc,qtr,f'Schedule_of_Investments_0.csv')):
            continue
        # qtr = '2022-12-31'
        print(qtr)

        index_list_sum = i = 0
        soi_files = sorted([
            os.path.join(bdc,qtr,file) 
            for file in os.listdir(os.path.join(bdc,qtr))
            if '.csv' in file
        ],key=lambda f: int(f.split('_')[-1].split('.')[0]))
        df = _clean(soi_files[i],remove_regex(qtr))
        index_list = df.apply(
            lambda row:row.astype(str).str.contains(stopping_criterion(qtr), case=False, na=False).any(),
            axis=1
        )
        index_list_sum = index_list.sum()
        dfs = [df]     
        i += 1
        cols = df.columns.tolist()
        while index_list_sum == 0:
            if '\\'.join(soi_files[i].split('\\')[-2:]) in exceptions():
                i += 1
                continue
            print(soi_files[i])
            df = _clean(soi_files[i],remove_regex(qtr))
            if set(list(range(10))) >= set(df.columns.tolist()):
                df.columns = cols
            dfs.append(df)
            index_list = df.apply(
                lambda row:row.astype(str).str.contains(stopping_criterion(qtr), case=False, na=False).any(),
                axis=1
            )
            index_list_sum = index_list.sum()
            i += 1
            
        date_final = dfs[0]
        if len(dfs) > 1:
            date_final = pd.concat(dfs,axis=0,ignore_index=True)#pd.DataFrame(concat(*dfs))
        # date_final = extract_subheaders(date_final,control=True)
        # date_final = extract_subheaders(date_final,control=False)

        date_final['qtr'] = qtr.split('\\')[-1]
        if not os.path.exists(os.path.join(bdc,qtr,'output')):
            os.makedirs(os.path.join(bdc,qtr,'output'))
        columns_to_drop = date_final.notna().sum() <= 2
        date_final.drop(columns=columns_to_drop[columns_to_drop].index)
        date_final.to_csv(os.path.join(bdc,qtr,'output',f'{qtr}.csv'),index=False)
        # break
    # Use glob to find files
    files = sorted(glob.glob(f'{cik}/*/output/*.csv'), key=extract_date)
    single_truth = pd.concat([
        pd.read_csv(df) for df in files
    ],axis=0,ignore_index=True)
    single_truth.drop(columns=single_truth.columns[['Unnamed' in col for col in single_truth.columns]],inplace=True)
    single_truth.to_csv(os.path.join(str(cik),f'{cik}_soi_table.csv'),index=False)
    
    
# from utils import init_logger
import warnings

# Suppress future warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.filterwarnings('ignore', category=pd.errors.SettingWithCopyWarning)
# init_logger()
main()

2014-03-31
C:\Users\pysol\Desktop\projects\sec_filings\1580345\2014-03-31\Schedule_of_Investments_1.csv


C:\Users\pysol\Desktop\projects\sec_filings\1580345\2014-03-31\Schedule_of_Investments_2.csv
C:\Users\pysol\Desktop\projects\sec_filings\1580345\2014-03-31\Schedule_of_Investments_3.csv


C:\Users\pysol\Desktop\projects\sec_filings\1580345\2014-03-31\Schedule_of_Investments_4.csv
C:\Users\pysol\Desktop\projects\sec_filings\1580345\2014-03-31\Schedule_of_Investments_5.csv


2014-06-30
C:\Users\pysol\Desktop\projects\sec_filings\1580345\2014-06-30\Schedule_of_Investments_1.csv


C:\Users\pysol\Desktop\projects\sec_filings\1580345\2014-06-30\Schedule_of_Investments_2.csv
C:\Users\pysol\Desktop\projects\sec_filings\1580345\2014-06-30\Schedule_of_Investments_3.csv


...

C:\Users\pysol\Desktop\projects\sec_filings\1580345\2024-03-31\Schedule_of_Investments_8.csv


C:\Users\pysol\Desktop\projects\sec_filings\1580345\2024-03-31\Schedule_of_Investments_9.csv


C:\Users\pysol\Desktop\projects\sec_filings\1580345\2024-03-31\Schedule_of_Investments_10.csv


C:\Users\pysol\Desktop\projects\sec_filings\1580345\2024-03-31\Schedule_of_Investments_11.csv
C:\Users\pysol\Desktop\projects\sec_filings\1580345\2024-03-31\Schedule_of_Investments_12.csv


C:\Users\pysol\Desktop\projects\sec_filings\1580345\2024-03-31\Schedule_of_Investments_13.csv


In [92]:

def remove_row_duplicates(row:pd.Series)->pd.Series: 
    out = []
    for v in row:
        if v in out:
            out.append(np.nan)
        else:
            out.append(v)
    return pd.Series(out)

# def remove_regex(qtr:str)->tuple:
#     if qtr in ['2023-06-30','2023-09-30','2023-12-31']:
#         return re.compile(r"TRIPLEPOINT VENTURE GROWTH BDC CORP\. AND SUBSIDIARIES\s+CONSOLIDATED SCHEDULE OF INVESTMENTS\s+\(dollars in thousands\)\s+(\(unaudited\)\s+)?As of\s+\w+\s+\d{1,2},\s+\d{4}")
#     regex_patterns = (
#         "^TRIPLEPOINT VENTURE GROWTH BDC CORP\. AND SUBSIDIARIES\s+CONSOLIDATED SCHEDULE OF INVESTMENTS\s+\((unaudited|dollars in thousands|in thousands)\)\s+\((unaudited|dollars in thousands|in thousands)\)?\s+As of (January|February|March|April|May|June|July|August|September|October|November|December) \d{1,2}, \d{4}$",
#         "TRIPLEPOINT\s+VENTURE\s+GROWTH\s+BDC\s+CORP\.\s+AND\s+SUBSIDIARIES\s+CONSOLIDATED\s+SCHEDULE\s+OF\s+INVESTMENTS\s+\(dollars\s+in\s+thousands\)\s+\(unaudited\)\s+As\s+of\s+March\s+31,\s+2023",
#         "TRIPLEPOINT\sVENTURE\sGROWTH\sBDC\sCORP\.\sAND\sSUBSIDIARIES\s\sCONSOLIDATED\sSCHEDULE\sOF\sINVESTMENTS\s\s\(dollars\sin\sthousands\)\s\sAs\sof\sDecember\s31,\s2023",
#         "TRIPLEPOINT\s+VENTURE\s+GROWTH\s+BDC\s+CORP\.\s+AND\s+SUBSIDIARIES\s+CONSOLIDATED\s+SCHEDULE\s+OF\s+INVESTMENTS\s+\(unaudited\)\s+\(dollars\s+in\s+thousands\)\s+As\s+of\s+March\s+31,\s+2024"
#     )
#     return re.compile(r'|'.join(regex_patterns) )
    
def _clean(
    file_path:str,
    regex_pattern:str=r"^TRIPLEPOINT VENTURE GROWTH BDC CORP\. AND SUBSIDIARIES\s+CONSOLIDATED SCHEDULE OF INVESTMENTS\s+\((unaudited|dollars in thousands|in thousands)\)\s+\((unaudited|dollars in thousands|in thousands)\)?\s+As of (January|February|March|April|May|June|July|August|September|October|November|December) \d{1,2}, \d{4}$|TRIPLEPOINT\s+VENTURE\s+GROWTH\s+BDC\s+CORP\.\s+AND\s+SUBSIDIARIES\s+CONSOLIDATED\s+SCHEDULE\s+OF\s+INVESTMENTS\s+\(dollars\s+in\s+thousands\)\s+\(unaudited\)\s+As\s+of\s+March\s+31,\s+2023|TRIPLEPOINT\s+VENTURE\s+GROWTH\s+BDC\s+CORP\.\s+AND\s+SUBSIDIARIES\s+CONSOLIDATED\s+SCHEDULE\s+OF\s+INVESTMENTS\s+\(unaudited\)\s+\(dollars\s+in\s+thousands\)\s+As\s+of\s+March\s+31,\s+2024"
)->pd.DataFrame:
    df = pd.read_csv(file_path,index_col=0,na_values=[' ', ''])
        
    df.replace(['\u200b',None, r'^\s*$'],np.nan,regex=True,inplace=True) #':','$','%'
    df.dropna(axis=0,how='all',inplace=True)
    
    df = df[~df.apply(lambda row:row.astype(str).str.match(regex_pattern).all(),axis=1)]
    important_fields,idx = get_key_fields(df)
    df.columns = important_fields
    df = merge_duplicate_columns(df).reset_index(drop=True)
    
    duplicate_idx = df.apply(lambda row:row[pd.to_numeric(row,errors='coerce').isna()].duplicated().sum() > 1 ,axis=1)
    clean_rows = df.loc[duplicate_idx].apply(remove_row_duplicates, axis=1).reset_index(drop=True)
    j = 0
    for i,flag in enumerate(duplicate_idx):
        if not flag:
            continue
        df.iloc[i,:] = clean_rows.loc[j,:]
        j += 1
    df.replace([r'^\s*$'],np.nan,regex=True,inplace=True) #':','$','%'
    df.dropna(axis=1,how='all',inplace=True)
    
    columns = (~df.isna()).sum(axis=0) <= 3 
    df.drop(columns=df.columns[columns],inplace=True)
    return df.reset_index(drop=True)

file_path = r'C:\Users\pysol\Desktop\projects\sec_filings\1580345\2022-12-31\Schedule_of_Investments_0.csv'
regex_pattern = remove_regex("2023-12-31")
df = _clean(file_path,regex_pattern=regex_pattern)
index_list = df.apply(
    lambda row:row.astype(str).str.contains(stopping_criterion('2023-12-31'), case=False, na=False).any(),
    axis=1
)
index_list_sum = index_list.sum()
print(index_list_sum)
display(df)


0


portfolio  \
0                                   Portfolio Company   
1                                    Debt Investments   
2                                Application Software   
3                       Flo Health UK Limited  (1)(3)   
4                                                 NaN   
5                                                 NaN   
6              Total Application Software -  5.40  %*   
7                      Business Applications Software   
8                                 Arcadia Power, Inc.   
9                                                 NaN   
10                                                NaN   
11                                                NaN   
12                                 FlashParking, Inc.   
13                                                NaN   
14                                                NaN   
15                                                NaN   
16                                                NaN   
17                                                NaN   
18                                         Hi.Q, Inc.   
19                                                NaN   
20                                                NaN   
21                                                NaN   
22                         Uniphore Technologies Inc.   
23                                                NaN   
24                                                NaN   
25  Total Business Applications Software -  19.67  %*   
26                     Business Products and Services   
27                                     Cart.com, Inc.   
28                                                NaN   
29                                                NaN   
30                         Quick Commerce Ltd  (1)(3)   
31                            RenoRun US Inc.  (1)(3)   
32                                                NaN   
33                                                NaN   
34  Total Business Products and Services -  11.51  %*   

                                           investment  \
0                                  Type of Investment   
1                                                 NaN   
2                                                 NaN   
3   Growth Capital Loan (Prime +  5.75  % interest...   
4   Growth Capital Loan (Prime +  5.75  % interest...   
5   Growth Capital Loan (Prime +  5.75  % interest...   
6                                                 NaN   
7                                                 NaN   
8   Growth Capital Loan (  8.75  % interest rate, ...   
9   Growth Capital Loan (  9.75  % interest rate, ...   
10  Growth Capital Loan (  11.00  % interest rate,...   
11                                                NaN   
12  Growth Capital Loan (Prime +  7.00  % interest...   
13  Growth Capital Loan (Prime +  5.00  % interest...   
14  Growth Capital Loan (Prime +  5.00  % interest...   
15  Growth Capital Loan (Prime +  5.00  % interest...   
16  Growth Capital Loan (Prime +  5.00  % interest...   
17                                                NaN   
18  Growth Capital Loan (  11.75  % interest rate,...   
19  Growth Capital Loan (Prime +  8.50  % interest...   
20  Growth Capital Loan (Prime +  8.00  % interest...   
21                                                NaN   
22  Growth Capital Loan (  11.00  % interest rate,...   
23  Growth Capital Loan (  11.00  % interest rate,...   
24                                                NaN   
25                                                NaN   
26                                                NaN   
27  Growth Capital Loan (Prime +  5.50  % interest...   
28  Growth Capital Loan (Prime + 7.25% interest ra...   
29                                                NaN   
30  Growth Capital Loan (Prime +  7.50  % interest...   
31  Growth Capital Loan (Prime +  10.50  % interes...   
32    Convertible Note (  4.00  % interest rate)  (2)   
33                                                NaN